In [1]:
import pickle
def rdPickle(filename):
    with open(filename, 'rb') as f:
        return pickle.load(f)

In [2]:
def mkPikle(filename, content):
    with open(filename, 'wb') as f:
        pickle.dump(content, f)
        f.close()

Read the values

In [3]:
_20news         = rdPickle('pickle/20News/_20news.pkl')
clean_corpus    = rdPickle('pickle/20News/clean_corpus1.pkl')
dict_           = rdPickle('pickle/20News/dict_1.pkl')
doc_term_matrix = rdPickle('pickle/20News/doc_term_matrix1.pkl')

** **
#### Step 6: Hyperparameter tuning
** **
First, let's differentiate between model hyperparameters and model parameters :

- `Model hyperparameters` can be thought of as settings for a machine learning algorithm that are tuned by the data scientist before training. Examples would be the number of trees in the random forest, or in our case, number of topics K

- `Model parameters` can be thought of as what the model learns during training, such as the weights for each word in a given topic.

Now that we have the baseline coherence score for the default LDA model, let's perform a series of sensitivity tests to help determine the following model hyperparameters: 
- Number of Topics (K)
- Dirichlet hyperparameter alpha: Document-Topic Density
- Dirichlet hyperparameter beta: Word-Topic Density

We'll perform these tests in sequence, one parameter at a time by keeping others constant and run them over the two difference validation corpus sets. We'll use `C_v` as our choice of metric for performance comparison 

In [4]:
import gensim
from gensim.models import CoherenceModel

In [5]:
# supporting function
def compute_coherence_values(corpus, dictionary, k, a, b):
    
    lda_model = gensim.models.LdaMulticore(corpus=doc_term_matrix,
                                           id2word=dictionary,
                                           num_topics=k, 
                                           random_state=100,
                                           chunksize=100,
                                           passes=10,
                                           alpha=a,
                                           eta=b)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=clean_corpus, dictionary=dictionary, coherence='c_v')
    
    return coherence_model_lda.get_coherence()

In [6]:
compute_coherence_values(clean_corpus, dict_, k=7, a=0.31, b=0.61)


0.47600907559509825

In [7]:
import pandas as pd
import os
import sys

In [24]:
#pd.DataFrame(model_results).to_csv(os.path.join(sys.path[0],'results/lda_20news_1.csv'), index=False)

In [17]:
import numpy as np
import tqdm

grid = {}
grid['Validation_Set'] = {}

# Topics range
min_topics = 2
max_topics = 22
step_size = 1
topics_range = range(min_topics, max_topics, step_size)

# Alpha parameter
alpha = list(np.arange(0.01, 1, 0.3))
alpha.append('symmetric')
alpha.append('asymmetric')

# Beta parameter
beta = list(np.arange(0.01, 1, 0.3))
beta.append('symmetric')

# Validation sets
num_of_docs = len(clean_corpus)
print(num_of_docs)
corpus_sets = [gensim.utils.ClippedCorpus(clean_corpus, int(num_of_docs*0.75)), 
               clean_corpus]
#print(corpus_sets)

corpus_title = ['75% Corpus', '100% Corpus']

model_results = {'Validation_Set': [],
                 'Topics': [],
                 'Alpha': [],
                 'Beta': [],
                 'Coherence': []
                }

# Can take a long time to run
if 1 == 1:
    pbar = tqdm.tqdm(total=(len(beta)*len(alpha)*len(topics_range)*len(corpus_title)))
    
    # iterate through validation corpuses
    for i in range(len(corpus_sets)):
        # iterate through number of topics
        for k in topics_range:
            # iterate through alpha values
            for a in alpha:
                # iterare through beta values
                for b in beta:
                    # get the coherence score for the given parameters
                    cv = compute_coherence_values(corpus=corpus_sets[i], dictionary=dict_, 
                                                  k=k, a=a, b=b)
                    
                    print(cv,k,a,b)
                    # Save the model results
                    model_results['Validation_Set'].append(corpus_title[i])
                    model_results['Topics'].append(k)
                    model_results['Alpha'].append(a)
                    model_results['Beta'].append(b)
                    model_results['Coherence'].append(cv)
                    
                    pbar.update(1)
    pd.DataFrame(model_results).to_csv(os.path.join(sys.path[0],'results/lda_20news_1.csv'), index=False)
    pbar.close()

11314


  0%|▏                                                                                                                                                                  | 1/1200 [00:10<3:32:29, 10.63s/it]

0.44476722839257643 2 0.01 0.01


  0%|▎                                                                                                                                                                  | 2/1200 [00:20<3:19:04,  9.97s/it]

0.44415924614017865 2 0.01 0.31


...

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊| 1199/1200 [9:45:27<00:48, 48.81s/it]

0.4084003752970389 21 asymmetric 0.9099999999999999


100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1200/1200 [9:46:19<00:00, 49.66s/it]

0.43229940901567365 21 asymmetric symmetric


NameError: name 'pd' is not defined

**Building a finetuned LDA model**

In [64]:
lda_model         = rdPickle('pickle/20News/lda_model.pkl')

In [9]:
# Build LDA model
# lda_model = gensim.models.LdaMulticore(corpus=doc_term_matrix,
#                                        id2word=dict_,
#                                        num_topics=7, 
#                                        random_state=100,
#                                        chunksize=100,
#                                        passes=10,
#                                         alpha=0.31,
#                                            eta=0.61,
#                                        per_word_topics=True)


In [65]:
# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=clean_corpus, dictionary=dict_, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('Coherence Score: ', coherence_lda)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [11]:
#mkPikle('pickle/20News/lda_model.pkl', lda_model)

In [66]:
num_topics = 7

import pyLDAvis.gensim_models
import pickle 
import pyLDAvis

# Visualize the topics
pyLDAvis.enable_notebook()

LDAvis_data_filepath = os.path.join(sys.path[0],'results/ldavis_med_'+str(num_topics))

# # this is a bit time consuming - make the if statement True
# # if you want to execute visualization prep yourself
if 1 == 1:
    LDAvis_prepared = pyLDAvis.gensim_models.prepare(lda_model, doc_term_matrix, dict_)
    with open(LDAvis_data_filepath, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)

# load the pre-prepared pyLDAvis data from disk
with open(LDAvis_data_filepath, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

#pyLDAvis.save_html(LDAvis_prepared, './results/ldavis_prepared_'+ str(num_topics) +'.html')
pyLDAvis.save_html(LDAvis_prepared, os.path.join(sys.path[0],'results/ldavis_med_'+str(num_topics)+'.html'))

LDAvis_prepared

/usr/local/lib/python3.9/dist-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/usr/lib/python3/dist-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alterna

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3     -0.164612 -0.065388       1        1  45.285827
6     -0.143385  0.063011       2        1  16.659920
4     -0.085950  0.080918       3        1  13.900653
2      0.030486 -0.160060       4        1   8.608160
0      0.040583  0.074451       5        1   7.336015
1      0.071814 -0.029621       6        1   5.574038
5      0.251064  0.036689       7        1   2.635388, topic_info=                 Term         Freq        Total Category  logprob  loglift
993        government  1246.000000  1246.000000  Default  30.0000  30.0000
1551            space   806.000000   806.000000  Default  29.0000  29.0000
1988              key  1440.000000  1440.000000  Default  28.0000  28.0000
1995             game   717.000000   717.000000  Default  27.0000  27.0000
357              chip  1058.000000  1058.000000  Default  26.0000  26.0000
3867             team   676.000000   676.000000  Default  25.0000  25.0000
178               law  1015.000000  1015.000000  Default  24.0000  24.0000
433               god  1973.000000  1973.000000  Default  23.0000  23.0000
326              year  1216.000000  1216.000000  Default  22.0000  22.0000
286            system  1787.000000  1787.000000  Default  21.0000  21.0000
436       information  1326.000000  1326.000000  Default  20.0000  20.0000
3116             file  1380.000000  1380.000000  Default  19.0000  19.0000
2333           window   776.000000   776.000000  Default  18.0000  18.0000
114             drive   829.000000   829.000000  Default  17.0000  17.0000
213               new  2248.000000  2248.000000  Default  16.0000  16.0000
1563        available  1175.000000  1175.000000  Default  15.0000  15.0000
229              play   517.000000   517.000000  Default  14.0000  14.0000
663               bit  1104.000000  1104.000000  Default  13.0000  13.0000
4028        president   668.000000   668.000000  Default  12.0000  12.0000
341            people  3871.000000  3871.000000  Default  11.0000  11.0000
649            server   590.000000   590.000000  Default  10.0000  10.0000
18               mail  1060.000000  1060.000000  Default   9.0000   9.0000
2128           season   395.000000   395.000000  Default   8.0000   8.0000
934           version   775.000000   775.000000  Default   7.0000   7.0000
452               gun   463.000000   463.000000  Default   6.0000   6.0000
22777      encryption   716.000000   716.000000  Default   5.0000   5.0000
144              good  2202.000000  2202.000000  Default   4.0000   4.0000
137               get  3101.000000  3101.000000  Default   3.0000   3.0000
445            thanks  1038.000000  1038.000000  Default   2.0000   2.0000
2257             card   604.000000   604.000000  Default   1.0000   1.0000
433               god  1970.527256  1973.882386   Topic1  -5.1439   0.7905
6687            faith   421.874676   424.842706   Topic1  -6.6852   0.7852
1574         religion   391.756049   394.988652   Topic1  -6.7593   0.7840
5685           church   490.194665   495.202930   Topic1  -6.5351   0.7820
1858           father   326.433817   330.118186   Topic1  -6.9417   0.7810
512         religious   288.439144   291.887989   Topic1  -7.0654   0.7803
8090           belief   237.215546   240.192319   Topic1  -7.2609   0.7797
2420            truth   388.276429   393.249283   Topic1  -6.7682   0.7794
1273            moral   240.179160   243.326916   Topic1  -7.2485   0.7792
3069             lord   228.208575   231.543456   Topic1  -7.2996   0.7777
6746             holy   195.393881   198.398474   Topic1  -7.4549   0.7769
4814           heaven   192.450298   195.512894   Topic1  -7.4701   0.7764
151              hell   338.494037   344.976202   Topic1  -6.9054   0.7732
20427       scripture   151.697778   154.661034   Topic1  -7.7080   0.7728
7577         catholic   158.568710   161.666935   Topic1  -7.6637   0.7728
7588             evil

In [70]:
from pprint import pprint

# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())

[(0,
  '0.012*"game" + 0.011*"team" + 0.009*"year" + 0.007*"play" + 0.007*"season" '
  '+ 0.006*"hockey" + 0.006*"new" + 0.005*"good" + 0.005*"league" + '
  '0.005*"last"'),
 (1,
  '0.015*"space" + 0.006*"information" + 0.006*"university" + '
  '0.006*"anonymous" + 0.005*"research" + 0.004*"privacy" + 0.004*"system" + '
  '0.004*"launch" + 0.004*"earth" + 0.003*"data"'),
 (2,
  '0.009*"government" + 0.007*"law" + 0.006*"new" + 0.006*"gun" + '
  '0.005*"encryption" + 0.005*"state" + 0.005*"national" + 0.004*"president" + '
  '0.004*"public" + 0.004*"administration"'),
 (3,
  '0.012*"would" + 0.011*"one" + 0.011*"people" + 0.007*"think" + 0.006*"like" '
  '+ 0.006*"know" + 0.006*"time" + 0.006*"god" + 0.005*"even" + 0.005*"well"'),
 (4,
  '0.007*"file" + 0.007*"available" + 0.006*"also" + 0.006*"window" + '
  '0.006*"get" + 0.006*"mail" + 0.006*"version" + 0.005*"server" + '
  '0.005*"program" + 0.005*"thanks"'),
 (5,
  '0.003*"medical" + 0.003*"disease" + 0.003*"cancer" + 0.002*"pain" +

In [71]:
# printing the topic associations with the documents
import operator
lstTopicsCorpus =[]

count = 0
for i in lda_model[doc_term_matrix]:
    print("doc : ",count, i[0])
    maxTopic = max(i[0],key=operator.itemgetter(1))[0]
    lstTopicsCorpus.append(maxTopic)
    count += 1

doc :  0 [(3, 0.3491894), (4, 0.6057614)]
doc :  1 [(0, 0.21345282), (2, 0.073317625), (3, 0.43457186), (4, 0.20384829), (6, 0.073479034)]
doc :  2 [(0, 0.010401947), (2, 0.010419747), (3, 0.661737), (4, 0.13823202), (6, 0.1610432)]
doc :  3 [(0, 0.034369666), (3, 0.35086727), (4, 0.31081486), (6, 0.2975317)]
doc :  4 [(0, 0.060152892), (1, 0.07482397), (2, 0.011824164), (3, 0.35407415), (4, 0.47558072), (5, 0.011218249), (6, 0.0123258745)]
doc :  5 [(3, 0.9512604)]
doc :  6 [(0, 0.029331105), (1, 0.029431418), (2, 0.030113902), (3, 0.038320255), (4, 0.8116575), (5, 0.028065704), (6, 0.033080135)]
doc :  7 [(0, 0.030386105), (3, 0.49906278), (4, 0.39963707), (6, 0.05787116)]
doc :  8 [(3, 0.5209565), (4, 0.43729395)]
doc :  9 [(0, 0.034899887), (1, 0.03246653), (2, 0.34438103), (3, 0.032899987), (4, 0.49317035), (5, 0.028055355), (6, 0.03412685)]
doc :  10 [(0, 0.02338866), (1, 0.019470135), (2, 0.020170478), (3, 0.30211815), (4, 0.23457605), (5, 0.019687593), (6, 0.38058892)]
doc :  1

doc :  188 [(4, 0.51933557), (6, 0.44791475)]
doc :  189 [(1, 0.03953577), (4, 0.95253587)]
doc :  190 [(0, 0.07448118), (1, 0.07506506), (2, 0.07458942), (3, 0.0755361), (4, 0.53796196), (5, 0.07564295), (6, 0.086723305)]
doc :  191 [(0, 0.0719427), (2, 0.16897242), (4, 0.74368834)]
doc :  192 [(0, 0.46892872), (1, 0.014391353), (2, 0.014799613), (3, 0.09613098), (4, 0.34587047), (5, 0.014223142), (6, 0.045655716)]
doc :  193 [(3, 0.36713478), (4, 0.5268708), (6, 0.0733596)]
doc :  194 [(0, 0.4158707), (1, 0.08266133), (2, 0.02942432), (3, 0.20197053), (4, 0.030125467), (5, 0.02934335), (6, 0.21060434)]
doc :  195 [(3, 0.4195939), (4, 0.5482152)]
doc :  196 [(0, 0.40007257), (1, 0.09861446), (2, 0.09942645), (3, 0.102558784), (4, 0.10039667), (5, 0.099183716), (6, 0.09974736)]
doc :  197 [(0, 0.015600238), (1, 0.015152935), (2, 0.014362989), (3, 0.33133996), (4, 0.5933996), (5, 0.0140840085), (6, 0.016060328)]
doc :  198 [(0, 0.01258818), (1, 0.012349174), (2, 0.012654286), (3, 0.8666

doc :  373 [(0, 0.03915747), (1, 0.040588934), (2, 0.039822686), (3, 0.61262953), (4, 0.043291822), (5, 0.038070697), (6, 0.18643887)]
doc :  374 [(0, 0.3580472), (1, 0.03220236), (2, 0.032100845), (3, 0.21486616), (4, 0.03903007), (5, 0.29100865), (6, 0.03274477)]
doc :  375 [(0, 0.09783117), (1, 0.09784006), (2, 0.09782323), (3, 0.09780426), (4, 0.09781711), (5, 0.09786938), (6, 0.41301477)]
doc :  376 [(0, 0.017115999), (1, 0.016554313), (2, 0.016944481), (3, 0.21955442), (4, 0.41588902), (5, 0.016412836), (6, 0.29752892)]
doc :  377 [(0, 0.010767527), (2, 0.020600323), (3, 0.33125386), (4, 0.12613504), (6, 0.49190736)]
doc :  378 [(0, 0.2557554), (1, 0.012080404), (2, 0.012594417), (3, 0.19064794), (4, 0.50356615), (5, 0.011960505), (6, 0.013395205)]
doc :  379 [(0, 0.026729085), (1, 0.02491244), (2, 0.024679992), (3, 0.48395422), (4, 0.38697034), (5, 0.023770772), (6, 0.028983112)]
doc :  380 [(0, 0.020427391), (1, 0.019561315), (2, 0.019605694), (3, 0.026193205), (4, 0.87093514),

doc :  585 [(3, 0.24217883), (4, 0.14940242), (6, 0.58813924)]
doc :  586 [(0, 0.017294422), (1, 0.016505653), (2, 0.017155698), (3, 0.6429408), (4, 0.01778381), (5, 0.016233156), (6, 0.27208644)]
doc :  587 [(0, 0.011784218), (1, 0.010696346), (2, 0.011603646), (3, 0.41574365), (4, 0.506734), (5, 0.030828733), (6, 0.012609409)]
doc :  588 [(0, 0.16606894), (3, 0.3268276), (4, 0.3525788), (6, 0.14340307)]
doc :  589 [(0, 0.09783117), (1, 0.09784006), (2, 0.09782323), (3, 0.09780426), (4, 0.09781711), (5, 0.09786938), (6, 0.4130148)]
doc :  590 [(3, 0.41553676), (4, 0.5063835), (6, 0.062491447)]
doc :  591 [(0, 0.26728907), (1, 0.027144821), (2, 0.026865702), (3, 0.38287508), (4, 0.24104501), (5, 0.02617305), (6, 0.028607264)]
doc :  592 [(0, 0.010702823), (2, 0.33101645), (4, 0.6217373)]
doc :  593 [(0, 0.023796622), (1, 0.050473407), (3, 0.79344285), (4, 0.11197709)]
doc :  594 [(6, 0.9475223)]
doc :  595 [(0, 0.072099715), (3, 0.4141775), (6, 0.5011949)]
doc :  596 [(3, 0.03326454), 

doc :  806 [(0, 0.013713726), (1, 0.012469733), (2, 0.013014805), (3, 0.15095444), (4, 0.26103476), (5, 0.011955335), (6, 0.5368572)]
doc :  807 [(0, 0.0584682), (1, 0.010231808), (3, 0.7038808), (4, 0.0101817865), (6, 0.19917892)]
doc :  808 [(0, 0.019281244), (1, 0.018984118), (2, 0.018714475), (3, 0.021968056), (4, 0.020300115), (5, 0.018118251), (6, 0.8826338)]
doc :  809 [(3, 0.19159184), (6, 0.77323604)]
doc :  810 [(3, 0.18265732), (6, 0.7804802)]
doc :  811 [(0, 0.013830545), (1, 0.013988616), (2, 0.0136951925), (3, 0.015126049), (4, 0.014436477), (5, 0.013435009), (6, 0.9154881)]
doc :  812 [(3, 0.21759956), (6, 0.75619364)]
doc :  813 [(6, 0.96065664)]
doc :  814 [(3, 0.8397428), (6, 0.1456445)]
doc :  815 [(0, 0.012205351), (1, 0.011592818), (2, 0.012320145), (3, 0.01273501), (4, 0.012253038), (5, 0.011458501), (6, 0.92743516)]
doc :  816 [(0, 0.025803868), (1, 0.025655866), (2, 0.025854744), (3, 0.2759472), (4, 0.027431916), (5, 0.025580892), (6, 0.5937255)]
doc :  817 [(3,

...

doc :  10606 [(0, 0.056090653), (1, 0.055673994), (2, 0.085864484), (3, 0.6426837), (4, 0.05377893), (5, 0.05081651), (6, 0.055091742)]
doc :  10607 [(0, 0.044582024), (1, 0.04346655), (2, 0.045426603), (3, 0.7352479), (4, 0.043473136), (5, 0.043398984), (6, 0.04440479)]
doc :  10608 [(1, 0.07010512), (3, 0.91059667)]
doc :  10609 [(2, 0.010313482), (3, 0.9428158)]
doc :  10610 [(0, 0.07664195), (1, 0.07503411), (2, 0.076945946), (3, 0.07537528), (4, 0.07471964), (5, 0.54659355), (6, 0.074689604)]
doc :  10611 [(2, 0.09488202), (3, 0.9043343)]
doc :  10612 [(0, 0.6133556), (1, 0.06303899), (2, 0.06693786), (3, 0.067644395), (4, 0.06356341), (5, 0.06032626), (6, 0.06513357)]
doc :  10613 [(2, 0.3023251), (3, 0.6941736)]
doc :  10614 [(2, 0.01026492), (3, 0.9419248), (4, 0.010060475)]
doc :  10615 [(0, 0.011304966), (1, 0.011780193), (2, 0.011054484), (3, 0.82461715), (4, 0.11867992), (5, 0.010762597), (6, 0.011800711)]
doc :  10616 [(2, 0.06353779), (3, 0.91041505)]
doc :  10617 [(1, 0.

doc :  10772 [(2, 0.032312527), (3, 0.45263153), (6, 0.50183177)]
doc :  10773 [(2, 0.64423996), (3, 0.037769612), (6, 0.31475064)]
doc :  10774 [(3, 0.4735201), (6, 0.50700086)]
doc :  10775 [(0, 0.014981467), (1, 0.015506562), (2, 0.017672002), (3, 0.017949512), (4, 0.016567929), (5, 0.014716026), (6, 0.9026065)]
doc :  10776 [(0, 0.010879968), (2, 0.09870598), (3, 0.729039), (6, 0.1333547)]
doc :  10777 [(0, 0.09783117), (1, 0.09784006), (2, 0.09782323), (3, 0.09780426), (4, 0.09781711), (5, 0.09786938), (6, 0.41301477)]
doc :  10778 [(3, 0.63223296), (6, 0.359667)]
doc :  10779 [(0, 0.024093011), (1, 0.25182137), (2, 0.03187831), (3, 0.4223702), (4, 0.21735404), (5, 0.023679776), (6, 0.028803272)]
doc :  10780 [(0, 0.034734327), (1, 0.03594166), (2, 0.036315847), (3, 0.037617136), (4, 0.038762458), (5, 0.034003243), (6, 0.7826253)]
doc :  10781 [(0, 0.011613346), (1, 0.011531369), (2, 0.011845919), (3, 0.37085962), (4, 0.0118646985), (5, 0.011485662), (6, 0.5707994)]
doc :  10782 [

doc :  10898 [(0, 0.01819075), (2, 0.3599484), (3, 0.29090056), (6, 0.32515338)]
doc :  10899 [(2, 0.07478611), (3, 0.381597), (4, 0.12774578), (6, 0.4000385)]
doc :  10900 [(1, 0.09439161), (3, 0.71565694), (6, 0.1632562)]
doc :  10901 [(3, 0.703778), (6, 0.25441322)]
doc :  10902 [(3, 0.95729357)]
doc :  10903 [(0, 0.01102941), (1, 0.055079777), (2, 0.24403462), (3, 0.6552569), (4, 0.011606253), (5, 0.010806189), (6, 0.012186781)]
doc :  10904 [(3, 0.20548186), (4, 0.3997884), (6, 0.3610612)]
doc :  10905 [(2, 0.28630164), (3, 0.58748), (6, 0.1199375)]
doc :  10906 [(1, 0.4054958), (3, 0.22047676), (6, 0.37165108)]
doc :  10907 [(0, 0.033808403), (1, 0.031130183), (2, 0.4063523), (3, 0.31445283), (4, 0.1460389), (5, 0.03213728), (6, 0.036080096)]
doc :  10908 [(2, 0.12045619), (3, 0.5948147), (6, 0.26218286)]
doc :  10909 [(3, 0.88037425), (6, 0.08817229)]
doc :  10910 [(1, 0.20444998), (3, 0.33368912), (6, 0.45641142)]
doc :  10911 [(2, 0.2456584), (3, 0.19720921), (4, 0.06301413), 

doc :  11041 [(2, 0.103939116), (3, 0.33460203), (6, 0.55120647)]
doc :  11042 [(3, 0.2854541), (6, 0.69626415)]
doc :  11043 [(3, 0.3552274), (6, 0.61779195)]
doc :  11044 [(2, 0.14665164), (3, 0.8158672)]
doc :  11045 [(2, 0.038160767), (3, 0.8625173), (6, 0.09460743)]
doc :  11046 [(0, 0.019309824), (1, 0.018688843), (2, 0.52032524), (3, 0.27118018), (4, 0.020191923), (5, 0.018437896), (6, 0.13186601)]
doc :  11047 [(0, 0.024318334), (1, 0.024760185), (2, 0.026230915), (3, 0.024996854), (4, 0.02447233), (5, 0.023563702), (6, 0.8516577)]
doc :  11048 [(2, 0.07220401), (3, 0.07709606), (6, 0.84549737)]
doc :  11049 [(0, 0.09783117), (1, 0.09784006), (2, 0.09782323), (3, 0.09780426), (4, 0.09781711), (5, 0.09786938), (6, 0.41301477)]
doc :  11050 [(3, 0.39370802), (6, 0.57313323)]
doc :  11051 [(0, 0.09783117), (1, 0.09784006), (2, 0.09782323), (3, 0.09780426), (4, 0.09781711), (5, 0.09786938), (6, 0.41301477)]
doc :  11052 [(3, 0.10205207), (4, 0.49472812), (6, 0.37277615)]
doc :  110

doc :  11199 [(2, 0.0134468535), (6, 0.9577216)]
doc :  11200 [(2, 0.06498399), (3, 0.89384353)]
doc :  11201 [(0, 0.025911773), (1, 0.025769942), (2, 0.34468266), (3, 0.46816033), (4, 0.08345314), (5, 0.023954827), (6, 0.028067341)]
doc :  11202 [(3, 0.7219094), (6, 0.2604247)]
doc :  11203 [(6, 0.96847653)]
doc :  11204 [(0, 0.011213902), (1, 0.028626963), (2, 0.16255787), (3, 0.18885426), (4, 0.079438366), (5, 0.041922014), (6, 0.48738664)]
doc :  11205 [(2, 0.106142424), (3, 0.7802647), (4, 0.089090824)]
doc :  11206 [(1, 0.033348285), (2, 0.17375302), (3, 0.37757444), (6, 0.39180595)]
doc :  11207 [(2, 0.13624223), (6, 0.8591935)]
doc :  11208 [(0, 0.71912277), (1, 0.047175627), (2, 0.044451464), (3, 0.053865995), (4, 0.04585685), (5, 0.043798994), (6, 0.04572831)]
doc :  11209 [(3, 0.28086665), (6, 0.69771117)]
doc :  11210 [(0, 0.01632753), (1, 0.018721586), (2, 0.016489927), (3, 0.43485108), (4, 0.05630838), (5, 0.0155624645), (6, 0.44173902)]
doc :  11211 [(2, 0.8231872), (6, 

In [72]:
lstTopicsCorpus[0:5]

[4, 3, 3, 3, 4]

**In this section we are merging the text corpus with the topic. So all the text rows topic will be tied up in one dataset**

In [73]:
df_Topic = rdPickle('pickle/20News/df_Topic.pkl')

In [75]:
corpus=[]
for cc in clean_corpus:
    corpus.append(" ".join(cc))

In [27]:
# df_Topic = pd.DataFrame(
#     {'Text': corpus,
#      'Cleaned_Text': clean_corpus,
#      'Topic': lstTopicsCorpus
#     })

In [76]:
df_Topic[3:5]

Text                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Cleaned_Text  Topic  high_sim_score  high_sim_position  high_sim_topic
3  excellent automatic found legacy sport mode electronics figure driver switch proper way sport mode entail several red line rev limiter case legacy lift briefly remain low gear handy charging would like without distraction another curve approaching part throttle based speed pedal depressed rather position pedal modern electronics measure easily switch sport mode wonderful want charge green light turn red well little half throttle right foot fast enough also think smart automatic deliver better gas mileage dumb driver stick else equal remember idea stick economical automatic big assumption driver smart enough know gear situation many time ridden inattentive driver highway gear speed many people drive really know best gear every conceivable situation sure know suspect chip automatic possible scenario ratio likely better also say previous proved wrong got car instantaneous high gear low wide open throttle economical low gear high small throttle opening explanation quite simple one think obvious first sight  [excellent, automatic, found, legacy, sport, mode, electronics, figure, driver, switch, proper, way, sport, mode, entail, several, red, line, rev, limiter, case, legacy, lift, briefly, remain, low, gear, handy, charging, would, like, without, distraction, another, curve, approaching, part, throttle, based, speed, pedal, depressed, rather, position, pedal, modern, electronics, measure, easily, switch, sport, mode, wonderful, want, charge, green, light, turn, red, well, little, half, throttle, right, foot, fast, enough, also, think, smart, automatic, deliver, better, gas, mileage, dumb, driver, stick, else, equal, remember, idea, stick, economical, automatic, big, assumption, driver, smart, enough, know, gear, situation, many, time, ridden, inattentive, driver, highway, gear, ...]      3        0.692777                295               4
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              ford automobile need information whether ford partially responsible car depletion ozone layer also additional information greatly thanks fault thank god innocent guy diesel otto feel guilty                                                                                                                                                                                                                                                                

In [18]:
#mkPikle('pickle/20News/df_Topic.pkl', df_Topic)

## Sentence Similarity Check

We will pick one sentence from one topic and check similarity among all the sentences

Try to find out where the test sentence is more similar

In [19]:
from sentence_transformers import SentenceTransformer

model_p = SentenceTransformer('sentence-transformers/all-mpnet-base-v2')

In [20]:
# Getting the embedding
q_emb = model_p.encode(df_Topic['Text'].tolist()[0])
p_emb = model_p.encode(df_Topic['Text'].tolist())

#### Create a function to display the statistics

In [21]:
from sentence_transformers import  util

def getSimiTopic(ind,p_emb):
    # Getting the embedding
    q_emb = model_p.encode(df_Topic['Text'].tolist()[ind])
    #p_emb = model_p.encode(df_Topic['Text'].tolist())
    
    print(df_Topic['Text'].tolist()[ind])
    
    # Printing the similarity score 
    sim_score = util.pytorch_cos_sim(q_emb, p_emb).cpu().detach().numpy()[0]
    
    # Data frame create
    df_Score = pd.DataFrame(
    {'Sim': sim_score,
     'Topic': lstTopicsCorpus
    })
    
    #display(df_Score.groupby(['Topic']).agg({"Sim": ['mean','sum','min','max','count']}))
    return df_Score.groupby(['Topic']).agg({"Sim": ['mean','sum','min','max','count']})

In [22]:
def getTopicScore(topic, p_emb):
    # We need a list of dataframes for each topic 
    lst_df  = []
    
    # Get the list of index in the dataframe for the selected topic
    lst_ind = df_Topic.loc[df_Topic['Topic'] == topic].index.tolist()
    
    for ind in lst_ind:
        print("added", ind)
        df = getSimiTopic(ind,p_emb)
        lst_df.append(df)
    return pd.concat(lst_df).groupby(level=0).mean()


In [21]:
# topic 0
getTopicScore(0,p_emb)

added 33
sale speed rear spoiler new best offer call
added 42
bird manual replace platinum every mart platinum real platinum bosch fiesta dad bronco note last long much le agree
added 43

added 55
long several ago two riding front pickup heading south interstate north someone threw rock overpass hit windshield accident sure impossible get overpass quickly see figured left couple ago guy company mid left behind wife turned reformatory away caught year old put cover overpass else could think forget story computer year old caught man insurance company could significant case interesting alt teen bach group music tri university meson facility voice mall campus university canada
added 68

added 129
think side mounted backup know ago friend certainly addition tail light mounted backup another set front turn signal assembly remember vintage enormous plastic growth size national geographic magazine sticking front fender incorporated amber parking amber side marker white like luxury towards side

added 1580
grandfather
added 1588

added 1604

added 1722
ditto
added 1758
pat yeah windscreen cut ended completely course environment space suck tommy mac radius vision circumference mystery
added 1838

added 1855
henry little joe big joe get built year little joe big joe thought saw something old film
added 1903

added 1911
first saw thought second headline star plier found recently know sometimes wire built tommy mac radius vision circumference mystery
added 1925
saw newspaper last night mae first black woman space physician chemical engineer flew last year appear transporter operator star trek next generation episode week may hardly space science know interesting
added 1953
advertising space romantic episode mead big ball wax watching constellation cola rising horizon slipped cause strike inspiration article formation space aesthetically desirable day aesthetic count count
added 1988

added 1992
yeah tore near house new beer drinking ghost still place one read ago
added 2007

added

like new sale offer trade
added 3864
rather disappointing
added 3971
good bad
added 3980

added 4009

added 4016

added 4118

added 4127

added 4142

added 4148

added 4185
white electronics would address work hpwbe wad phone address analytic division
added 4200
yep
added 4231

added 4269

added 4339

added 4390
pearl mun
added 4397

added 4424

added 4432
simply min sum subtract sum hpwbe wad phone address analytic division
added 4479

added 4672
word subrogation willing wait money insurance save pay deductible however insurance scum insurance may pay deductible get insurance pack rabid large fanged recover damage scum insurance sad true call job security later
added 4683
bolt bottom barrel tap coffee could rev engine boiling pour cup hot water used ethylene glycol antifreeze rather
added 4689
bought rg abruptly grad student first sold truck yesterday need sell zephyr sell month great insurance run couple otherwise tag insure see sweet bike almost highway last summer plus great border

added 5021
diving one
added 5023
sorry specific ran last small twin got based twin ran creditable modern put high ran mid latest crop run hard remember new goof clobber old handily top end roll technology still one
added 5028

added 5032
ford anemic mid sized car name back last decade rented one car would ruin name zephyr rod
added 5034
drinking riding new york limit
added 5052
hell save candle bring light dribble wax kindling wood light that although like belly button lint eggshell case idea best feeling particularly industrious eventful evening one soggy summer open fuel line drain onto piece rough rotten wood stick middle soon inferno carefully strike match titled one latter cat cradle work like charm every time
added 5057
usually wear inside full face helmet keep dirt wind mumble mumble mumble
added 5058
problem back rode barcelona back two stroke back representative size road considered big bike day anything bigger real rare smith dod kspt
added 5064
heavy beginner bike except may

looking singer featherweight sewing machine old black sewing machine black case please contact
added 5684
final public update dragon magazine auction new current stand like happen mail entire auction end soon stop coming want get sure bid must made least cent buyer pay shipping unless particular fancy mail class special lot padding bagged condition vary quite bit come condition system may missing like feel free ask condition usually evaluation cover material inside great shape excellent find store good still great condition tell boughten good line fair fair lot still decent poor material inside may usually scissors condition something magazine missing usually insert post another public update sometime weekend final public posting auction mail bidding ask away arrow fair top secret module missing bard real good forest doom module detached included inner good combat computer missing good aquatic module detached included language lesson good top secret module detached included magic resis

...

added 8834
lot carry man roster catcher seldom ever used insurance case extra catcher injured game free roster spot extra pinch hitter reliever invoke catcher substitution rule last roster catcher team injured game team permitted substitute place defensive catcher previously game given rule team need roster catcher could non roster catcher
added 8837
left list team large extent frank hit first lose lot anyways many place known drive happen often unlikely white front
added 8842
run completely time got get one worse last year prediction contest east well long hard came blue going wrong direction bring pick fluke ready red bad last year get better pitching new definition replacement level really think win matter fact see team league winning either division paper possible exception hate body win pick really think going repeat prediction expectation big cal insane yes without ado strong getting rid billy weak may start original something may fifth starter best bottom anybody else think migh

happen big fan stark baseball writer inquirer every week review column unusual week unusual section week stupid ralph every year contest last guy get hit also baseball column sort week review check column sometime might make laugh rob
added 8908
since everyone else running wild decided add fuel fire might seem bit normal albeit small league east new york blue boston red league west city white athletics young rookie year salmon manager year buck comeback player year national league east new york national league west san san colorado barry young rookie year manager year joe comeback player year eric world heart brain win division lose win series stick way
added 8911
educate rip manager year injured previous game resting far whitten controversy whitten power jordan hit way find starting soon enough sam
added 8915
well excellent shutout justice drove run single first get ready monster year ball opposite field lot power natural power right field good batting eye stay healthy back full stren

added 9001
went game tonight cap night control trouble night first batter second single scored run batter taking second throw home another single made score tried new line butler reed piazza batting third eric favor webster piazza first make score tied game second two single fourth inning already made score still dodger defense made several impressive piazza great behind plate gunning runner trying steal second throwing runner first bit first base also made spectacular play keeping ball going outfield runner first sure ball going kept running past second got threw third easily got runner third heart sank gross got warm pinch hitter gross game score still dodger knew gross relieving stunk pitching forcing much inning game effect next night gross fresh given light work gross lived name first batter gave hit second base loaded grounder force home scoring fly ball make gross little attention next thing knew stolen fourth run runner first eventually tagged run run scored long meanwhile moun

added 9075
good collapse somewhat come back next year went era era around well several lost year record source bill historical baseball abstract let forget finished pretty bad era take stadium account start season recall era half era half last year suppose game next era end year think right going hard come back hunch morris may pitching injury telling anyone guess remainder season perhaps come cox went scoreless tribe today start morris like really good one scrambling find imagine luckily good offense think would dare release end year cox
added 9078
yesterday national west lost last streak home road san lost colorado lost san lost national east lost lost lost new york lost west lost last streak home road lost lost white athletics lost lost city lost east boston red lost new york blue lost lost yesterday idle listed alphabetical order national league league new york white boston red city colorado blue san new york athletics san rain soda
added 9082
think grand slam result new fan club l

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.166530  165.197357 -0.081781  0.999316   992.0
1      0.095311   21.730955 -0.077068  0.314261   228.0
2      0.097515   30.229774 -0.083023  0.359815   310.0
3      0.096872  501.019745 -0.137601  0.522308  5172.0
4      0.079432  135.430984 -0.117795  0.421571  1705.0
5      0.091015    8.828485 -0.065531  0.299865    97.0
6      0.074206  208.520157 -0.127240  0.416541  2810.0

In [22]:
getTopicScore(1,p_emb)

added 370
article ejvj
added 388
buy computer rather horrid viscous coupled outgoing
added 576
request discussion request discussion creation concerning allow exchange information group name status rationale may enough people interested interested knowing reason justify new recent growth net could improve turnaround time posing question community discussion new posted news reader able may mailed proposer address voting arise voting start month posting date proposer tommy tommy
added 627
test
added 766
generic optical access international west park suite polk street suite san optical medium international drive architecture place north creek parkway suite dev send message someone form address apple address appropriate address
added 924
day ago freeze inactivity stay alive long program actively running long mouse anyone experience similar known please reply read normally mike fisher frank senior research fellow institute technology technological university avenue
added 1099
usually left h

added 1618
call navy scientific visualization virtual reality seminar june division naval surface warfare center formerly research center sponsor ness navy engineering system one day navy scientific visualization virtual reality seminar purpose seminar present exchange information navy related scientific visualization virtual reality research solicited navy related scientific visualization virtual reality current work work progress work navy considered four available regular presentation length short presentation length video presentation stand alone author need attend seminar scientific visualization virtual reality demonstration accepted however seminar submit one page abstract naval surface warfare center division code voice mail navy mil include type presentation telephone author designate one point contact submission deadline notification acceptance sent may reproduction must received june information contact address please distribute widely possible thanks navy mil model basin li

archive name space astronaut last date become astronaut first short form henry spencer official announcement become astronaut assume mean astronaut since probably impossible non get corp paying professional fly even better win lottery becoming shuttle pilot lot fast jet experience military flying career forget unless want anyway want become shuttle mission specialist citizen become one must crucial thing remember demand vastly supply problem finding qualified people thinning manageable length enough qualified must avoid dis qualified reason many principle quite irrelevant job get specialize something getting dirty equipment paper pencil forget computer entirely done ground fore seeable future degree one field plus work experience another frequent winner good physical condition good eyesight get radial similar hack improve vision nobody sudden pressure would long term effect poorly understood matter avoid significant medical pas jet pilot physical poor public speaking conservative confo

lunar satellite need fuel regular orbit fuel crash within noticeably lunar lasting day possible stable moon gravitational field poorly know none sun earth relatively minor low big problem moon gravitational field quite lumpy due irregular distribution mass within moon
added 1818
estimate probability project peak observatory maybe century could gamma ray spectroscopy distant observatory primitive send probe get gamma ray spectroscopy done television yet
added 1824
launch complex gosh polish way brazil joke space agency send astronaut surface sun thing solve sending man surface sun simple travelled night
added 1826
proton used stage two stage version used first stage used today four stage version used mostly escape stage version used low earth since version mir add mir long centaur smaller mir believe fit shroud vaguely recall lox upper stage proton
added 1830
essay writing space shuttle need better propulsion system research found rather clumsy launch safety sitting hydrogen bomb curren

posted david lunar tele operation model one ltm march introduction order increase public interest space based lunar real miniature lunar like environment test tele remotely world wide personal provide test bed simple tele operation tele presence also information operating space limited layout lunar colony tele operating work play educational information providing creativity achievement new way participate twenty first century remote learning nature ltm project people contribute scenery electronics graphic operation ltm playground laboratory used personal computer home terminal institution user able tele operate real ltm base experimental recreational real facility ample opportunity provided medium coverage construction lunar model operation new added broad inherent interest wide range tele virtual reality research radio control model railroad ham radio operation astronomy space science art theater network game model child ltm overall design room base lunar layout used distant moon star

...

added 7046
bet runway nearby
added 7075
month ago photo posted alt inch northern pike caught lure made
added 7156
country es ce phone
added 7200
spell tuna helper
added 7237
buy chip name address dan may say something profound environmental science one day university western essun phone
added 7299
handbook radio amateur getting solid state design radio amateur
added 7397
content table following part program user interface simulation system work cause version know used instead caught net time formerly since program zero width height error trouble shooter computation modelinittable table though label exist width height zero thus following cannot perform anything else set width height newly zero wonder child create zero width height dependent whether width height shell set resource file question anyone know low working table perhaps happy someone able help answer german kaiser kaiser part interest model old width height parent troubling table relict age modelinitpoppedup modelinitformview

following posting forged name please ignore forged soc culture talk politics talk politics forged soviet soc culture forged forged news forged organization university center forged date forged forged forged dear forged forged graduate student education university forged forged forged forged questionnaire forged teaching music deaf forged forged name forged address mail forged institution forged experience grade level forged educational background bachelor master doctorate forged professional field special music posting forged name please ignore
added 9966
joy cold blooded genocide million people criminal think could cover genocide fascist never soviet today longer single soul power tear away veil illusion create certainly possible severe artificial life support system ethnic purity falsely trust structure support heart alien land purity first world war dictatorship systematic genocide tried complete old policy annihilation savagely murdering million rest year homeland attempt genocide 

added 10970
archive name net privacy part last version identity privacy anonymity commercial except permission author otherwise may freely copied please credit summary account privacy anonymity file encryption academic computer relevant legislation privacy associated global general search exact section search underline next section part file related privacy learn cryptography list privacy related privacy enhanced mail request related privacy run anonymous privacy anonymous message program miscellaneous digital cash hacker cracker steganography anonymous security obscurity identity guard electronic privacy electronic frontier foundation computer social responsibility operation sun devil game case digital network national research education network digital telephony act legislation related privacy academic freedom archive background behind anarchy like language list change history related privacy information type man apropos shell prompt change password finger obtain information remote u

added 11081
conference announcement final call thirteenth annual conference international association research computer society technical committee security privacy computer science department university bell northern research subsidiary northern campus university august original research technical expository solicited practical theoretical cryptology may also special invitation program committee send detailed abstract full paper program chair address given limit type counting bibliography title page must arrive time later sent airmail order receive consideration program committee start succinct statement problem solution significance cryptology appropriate non specialist reader technical development directed specialist follow eligible submission must anonymous appear title page submission possible remove page send program committee latex style file output format available program chair informed acceptance rejection letter mailed june compilation accepted available conference form acce

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.095347   94.584671 -0.104883  0.414734   992.0
1      0.203288   46.349628 -0.048242  1.000000   228.0
2      0.137056   42.487381 -0.069999  0.442316   310.0
3      0.108468  560.997742 -0.137015  0.551484  5172.0
4      0.112667  192.096893 -0.110762  0.518333  1705.0
5      0.095356    9.249578 -0.063931  0.295343    97.0
6      0.097796  274.808044 -0.115945  0.479320  2810.0

In [23]:
getTopicScore(2,p_emb)

added 20
today
added 247
test durant durant took successful company little known fact actually took durant got back charge legally new company division sloan era board superior always degree autonomy given chevy division presumably initial structure look organization chart sloan book chevy division directly floor passenger car division
added 261
built like city medium large small handful two shah
added 270
according representative saw recently must authorized dealer one roughly car
added 294
carrying pistol loaded unloaded glove compartment considered carrying concealed weapon colorado illegal without concealed permit unless law recently carrying weapon openly legal colorado illegal read newspaper account last year police stopped car traffic infraction magnum revolver sitting seat driver could possessing carrying weapon concealed article stated gun discovered glove box would considered crime
added 1606
small six nine
added 1667
forty two six time nine
added 1793
following press release

could public missile michigan description like talking high power rocketry outgrowth model rocketry hobby non metallic structural ranging impulse classification hobby flourishing early becoming increasing popular technically consider amateur rocketry rocket weight greater total impulse greater waiver launch typically group people get waiver period time week weekend site time covered blanket waiver also high power safety code specific launch field size finally order purchase class rocket need certified either national association rocketry tripoli rocketry association certification require handling safe flight total impulse level information watch
added 2286
bit reprocess nuclear fuel get plant bomb grade plutonium also given current simply fabricate new fuel rather reprocess old potentially dangerous national security point view fabricate back fuel plutonium may result something may kind boom hardly decent bomb grade plutonium want bomb grade plutonium research reactor power reactor wan

stuff clarification obfuscation actually well regulated necessary security free state present participle used adjective modify militia main clause sentence right verb shall right keep bear arm essential sentence restrict right state imply possession right anyone anything people make positive statement regarding right people people first fourth ninth tenth well second amendment existence right assumed amendment stated condition right bear arm necessity well regulated militia security free state entire sentence right keep bear arm unconditional final word belong many constitution otherwise majority ensue popular opinion concept familiar federalist
added 2485
several way one choose issue original intent subjectively political day original intent basis constitution clear founding intended individual citizen bear arm similar used day cite federalist second yale law review prof sorry date handy prof sought prove convey individual right hence title report united congress second session suprem

well going discus police officer today police feloniously accidentally apparently everybody year rate police one officer one officer one officer two foreign one officer two foreign one officer one federal officer god love information age
added 2572
debate second amendment continue well regulated militia practical however authority area binding court decision matter even decision area higher court anyone legal precedent preferably supreme court decision specific meaning amendment
added 2573
libertarian second amendment caucus fort collins colorado questionnaire city council upcoming election know watching feel free strike fancy inspiration would willing state writing publicly oath office would resign never run office group come individual would support city charter amendment city government force human reason please put following list order precedence highest city ordinance city resolution state law federal statute constitution state constitution believe appropriate city official employ

added 2705
wondering reason support following previous mail letter make sure support something really strongly support following currently considered congress would either positive effect towards reducing crime enforce constitutional right amendment amend title united code provide mandatory minimum sentence unlawful possession firearm felon fugitive justice person addicted unlawful user substance transferor receiver stolen firearm increase general penalty violation federal increase enhanced provided possession firearm connection crime violence drug crime smith restore second amendment specter provide federal drive kohl amend section title united code make federal crime steal firearm interstate foreign commerce bill colorado coalition story bout man took bullet head even though act perfectly normal pretend brain dead story bout woman nothing sit around day husband medium martyr take away bunch bunch got stuck bunch
added 2707
first move incident bomb several gunfire circa mayor white fr

...

eager hear legal theory behind exchange cryptographic data given first theory behind personal encryption one personal even le tenable perhaps make treaty say iceland restrict paraphernalia good end run around constitution happen someone pointed force law land like bill amendment congress shall make law respecting establishment religion free exercise thereof freedom speech press right people peaceably assemble petition government redress amendment well regulated militia necessary security free state right people keep bear arm shall amendment soldier shall time peace quartered house without consent owner time war manner law amendment right people secure effect unreasonable shall shall issue upon probable cause oath affirmation particularly place amendment person shall answer capital otherwise infamous crime unless presentment indictment grand jury except land naval militia actual service time war public danger shall person twice put jeopardy life limb shall criminal case witness life lib

article news effector carl initial analysis privacy security proposal administration today made major announcement cryptography policy effect privacy security million first part plan begin comprehensive inquiry major privacy export effectively people easy access robust encryption well law enforcement new technology however concerned administration already conclusion one critical part inquiry public comment discussion apparently administration going leverage get telephone equipment adopt voice encryption standard national security agency clipper chip bit split key encryption scheme built chip military contractor two separate escrow would store turn law enforcement upon presentation valid warrant encryption scheme used classified chip available manufacturer incorporation proposal number serious first administration solution inquiry clipper chip may secure product may better furthermore rely government sole source clipper chip rather independent chip able produce based open second algorit

try reading strong angling next honestly see hint sophisticated encryption technology used protect electronic fund transfer used protect electronic mail computer encryption hint new technology help protect proprietary information protect privacy personal phone prevent unauthorized release data time technology privacy need employ voice data encryption business ability authorized access telephone data proper court legal order necessary protect big hint administration working private sector spur development national information infrastructure new computer give unprecedented access information infrastructure high speed information transmit video huge data easily today telephone system voice big hint see since encryption technology play increasingly important role infrastructure federal government must act quickly develop consistent comprehensive regarding conceivable meaning particular technology computer network intend used exclusion encryption disagree reason already place besides even r

random passing thought anyone cite encryption technology excluding contra gang sfsuvax
added 11307
perhaps escrow come really interesting example hope physical process come truly random come trap door could drive truck either following starting question computer call public debate new government encryption initiative computer social responsibility today public disclosure technical data underlying government newly public encryption management initiative new cryptography scheme today white house national institute technology implement technical plan spokesman acknowledged national security agency super secret military intelligence agency actually encryption technology around new initiative built according technical presidential directive plan classified open initiative public review debate today series freedom information act key national security council information encryption plan keeping spirit computer security act congress order open development non military computer security public

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.097518   96.737923 -0.100265  0.409481   992.0
1      0.137301   31.304707 -0.071137  0.447556   228.0
2      0.210876   65.371483 -0.056406  1.000000   310.0
3      0.143963  744.577087 -0.130882  0.634268  5172.0
4      0.085826  146.332870 -0.118332  0.445903  1705.0
5      0.114955   11.150620 -0.057236  0.319591    97.0
6      0.074886  210.429993 -0.126425  0.445017  2810.0

In [24]:
getTopicScore(3,p_emb)

added 1
recently posted article kind single male old paying performance summary received close enough dodge stealth twin turbo model house taken defensive driving security alarm single year state farm insurance additional umbrella policy car house base policy standard policy defensive driving course le bought car company never accident ticket hope university hope name correctly insurance performance well last year similar situation bought car made inquiry age car eagle talon awd driving record clean state cost turn may insurance go also single higher rate company got couple pay different also maybe lucky hope dan mot cellular subscriber group live drive thunderbird never made claim insurance though hit several time negligent see stop fiddling three moving last one going one failure clear intersection still say damn light yellow one going record state farm passive restraint deduction liability deductible comprehensive deductible collision roughly year paying year escort law center aardv

something going month group must get specific detailed question would like ask next month get one instead honda thank
added 37
turbo good mph useful blowing away though believe beetle better say without doubt never blown away ever blocked car though head thought happen car
added 41
look motor trend time right along car small inch weather xgtv mention better time also vary magazine magazine road track car driver road track also quarter mile time vary tell exactly furthermore outrun high end car driver road track fast always believe exact drive see self low high gearing make difference still call torque though quad reliable yeah definition reliable reliable safe say general near perfect mention hell smoother quieter balance engine contest rev car day everyday never blow hose crack block anything else speak saying quad bad engine highlight reliability engine better investment since hold value considerably much better nice job sporty car practical time
added 46
sure since beast tell anothe

good point idea either handle reach however high quite amenable long high speed done several mile civic whatsoever last big trip made driving new york remember driving day typically without sure would comfortable driving white trip back new way surprising good fuel economy high see difference sustained sustained mph trip back new got quite mind engine almost civic markedly better fuel economy road still get driving compare diesel gasoline engine see enough gasoline sale advertise rebuilt honda build accord darn well expect sucker last ever got caught behind early sdl stop light pleasant lot better though diesel probably economy care gas cheap personally buy diesel car reason buy somerset
added 95
reverse warn backing bright enough typically see without brake tail well red orange already taken maybe white direction car moving really want able see behind get fog back car work well good way get rid get rush testosterone
added 96
hate rehash old thread would someone kindly quote dealer civ

added 150
agree fully loaded would come close price lower end ford fully loaded hand would still substantially expensive even fully loaded would run somewhere around fully loaded would somewhere around range base believe might start around course sho push really try totally different car sedan statement entirely faulty little inaccurate well least dealer like seem rationally picked car best aging design wagon probably got good deal one last
added 152
motivation already selling every car make multiple plant given possible motivation could lower
added 158
car ago liquid wax got wax black plastic molding tried repeatedly remove luck verge molding altogether nice car armor wax protege black plastic mileage may vary given observation one would well advised take care get probably similar son gun one paint
added 159
painted told refrain waxing leave sun supposedly let escape paint month smell away hot day slight surface flow paint remains little soft
added 162
significantly le value many argu

honda especially deal
added 236
thing turbo new budget
added 237
sound good leave grit oil pan also told change old hot grit much time settle
added 240
exactly service incident similar experience recently bought new truck picked vehicle little agreed price wrote check payment plus tax license told back evening pick truck returned wait hour finance guy could get finally got everything went smoothly discovered tax license said another said already agreed price problem giving money finance guy similar thing year ago bought used ford bronco since stolen took delivery sent letter telling license renewal need send check avoid delay registration thing already received pink slip received another letter phone coming first finance guy general manager hounding extra money left alone told already pointed clause contract stated final price final budge told another deal right told call would business future seem problem used ford dealership much better experience new pathfinder month ago certainly b

...

added 11127
great nice choice bad convince everyone bad unrestricted encryption child molester instead course word suspect never used guess people already operating drug ring jail question instead suppose law enforcement agency political opponent senior administration official conversation interpretation event yes presence clipper chip change give people talking phone false sense security also give federal law enforcement justification deny strong encryption inconvenient dang supposed inconvenient impossible sure way make sure still legitimate law enforcement access huh sure predict within two chip debut full technical posted crypt impact security key escrow system lied worth salt withstand light public scrutiny way sure algorithm unrecognized unless half world trying break decade even careful
added 11128
might get begin government really le political right wing pro establishment could think would interested political would recruit give government line history people start mechanism ad

recent post saw alt privacy clipper hope anyone interested topic clipper development four however little put name monstrosity even get door matter already hope take time voice extreme displeasure well
added 11192
message clipper chip come following address clipper clipper chip announcement rather computer list name brevity well interesting marc government suppose anybody within would care comment white house idea cruel joke know least one person list first clipper morning newspaper another already fired letter protest point suspect list interesting various represent cabal put proposal together yes may nothing list people get related mean may
added 11193
think new organization would much better idea much baggage hot shot reputable reading message effective group come existence count
added 11194
interesting message effect clipper chip state local police actually reading could good thing civil one respect since least prevent cowboy cowboy state local reading traffic tap illegally extensiv

sure recent found yet market early remember big scandal year two ago exactly
added 11234
nice think naive fact million people today sending highly confidential information easy receive cellular figure small risk people understand way least crypt good believe send important stuff thankful longer clear voice cellular tiny fraction people want worse government spook level secure may indeed reason could possibly want extra level avoid police attract attention likely lawbreaker suspect suddenly another level cryptography tap phone must something hide please sign warrant search house
added 11235
murder instead copyright violation keep straight criminal copyright civil sorry waste quibble want anyone get confused think bunch make better test case bunch criminal distribution
added 11236
seem assuming equal value spread uniformly among
added 11240
wonder landed fat fee design care course take care well person undefined usefulness elimination becomes consideration
added 11246
quick reality check

added 11300
think regime highly relevant many people sand saying cannot happen constitutional every day government end run around crisis drastic action likely future possession secure encryption possession terrorist drug serious felony like common police say common computer even become terrorist bet someone lived important go way old soviet union client far individual privacy overall freedom concerned rest world remember new world order far behind please keep posting anything find deficient thing example conversation suspect lawyer longer private big brother eavesdropping political dissent dangerous country government decide enough people take one seriously one becomes guilty plotting overthrow government illegal phrase illegal defined whatever government defined couple pressing smart national card internal passport added wrinkle anything past put take government word really since completely read thing nice bust one safe without owner safe broken break secure phone data near future way

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.096863   96.087845 -0.102096  0.395111   992.0
1      0.108496   24.736979 -0.075769  0.376999   228.0
2      0.143964   44.628716 -0.071489  0.435185   310.0
3      0.145312  751.554688 -0.124448  0.999933  5172.0
4      0.080049  136.483994 -0.118390  0.419618  1705.0
5      0.122670   11.899011 -0.052846  0.338166    97.0
6      0.078657  221.026337 -0.120535  0.407061  2810.0

In [25]:
getTopicScore(4,p_emb)

added 0
wondering anyone could enlighten car saw day door sport car late early really small addition front bumper separate rest body know anyone model name engine spec production car made history whatever funky looking car please mail
added 4
ford automobile need information whether ford partially responsible car depletion ozone layer also additional information greatly thanks fault thank god innocent guy diesel otto feel guilty
added 6
avoid entirely oil drain valve place bolt one combined
added 9
addition restricted mileage many classic insurance also require vehicle
added 12
additional data point run exclusively following rabbit rabbit bus beetle bus never oil related problem disclaimer mighty hot
added 15
mentor tommy advise automobile search dependable automobile purchase smaller engine tony
added 17
manta two door sedan engine sometimes manta also hot fun
added 18
sorry last post server send message
added 19
article colorado eric let put like similarity three liter engine displac

added 73
recently lemon aid new car guide found car would given picture later driver passenger virtually front end collision highly small car civic worst crash rating small listed many great survive accident safety one important car
added 74
ford tried also back ranger pickup horn end turn signal stalk instead center wheel god intended drove two different never get used pushing turn signal stalk blow horn time got right getting annual state safety inspection one ford better
added 76
diamond star talon eclipse laser put turbo awd turbo also handling match muscle civil regular driving rather harsh stiff ride awd turbo clearly better choice two torque steer front drive model may leftover slightly used model price range tough decision rob rwf
added 83
archive name part automotive archive server automotive archive server process presently available
added 84
write auto transmission still think half auto may right nothing whatever auto transmission normal manual transmission gearbox clutch se

two check see wear problem area pas penny test guide problem wet call may enough tread left channel water tire go fishy road age particular soft tire get harder put heat harder grip well soft effect get hot often competition
added 160
number based case need call assistance earth source car send free
added 161
everybody buy honda civic coupe dealer ask stereo tax registration live time lot compare dealer good price car much pay please mail want post thanks lot mtecv
added 166
want start list typhoon interested please contact via mail
added 170
let add ford garage work well factory identical mine people result know probable ford
added 171
turbo model come wagon quick wagon rare also
added 173
prefer manual automatic believe people physical otherwise would able drive automatic allow lazy time available fiddle radio look scenery instead road manual transmission drive always something large movement plus driving fun driving manual fun driving automatic chore case shift speed made shift far 

added 210
rubber drain carpet like spare probe put silicone sealant put back
added 212
someone working electronic odometer design based system write somewhat pattern idea make circuit difficult program arbitrary secondary purpose primary purpose standpoint practicality distributed avoid maximum number used also coming hall effect rate higher make reading bench least somewhat undesirable automobile ever exceed operation case course might indeed store since steering angle velocity data available would difficult collect interesting demographic information car aware manufacturer currently trying enforce warranty based reading data could potential invasion privacy access data driving style could also provide valuable information actual field help engineer appropriate personally mind dealer driving long done anonymous fashion
added 216
looking jeep wondering anyone bad good model much different like nice vehicle even thought price rather steep
added 224
would concerned car driven well one wo

added 255
yes consumer confusion early fuel crisis everyone better fuel mileage diesel fuel fuel available usually better mileage comparable gasoline decided gas engine diesel engine think liter big mistake engine converted engine could handle higher compression lot thew big red flag casual observer buy diesel bad gross generalization ask question livelihood driving lot would dependable undependable short run vehicle greyhound trailer truck even train gasoline diesel tractor trailer truck provide mile warrantee diesel suburban diesel great engine going expensive new gasoline engine vehicle problem diesel need rebuilt expensive gas engine pay rebuild diesel diesel engine twice long better mileage carburator gasoline engine rebuild le rebuild fuel injection pump diesel cost never need tune looking rebuilt say got great deal check see fuel injection pump rebuilt also
added 258
transmission car get much acceleration let convertor lockup induce briefly lifting quickly quickly trigger thrott

...

added 7810
dear application motif slider select image file directory would like display name file corresponding value dragged scale button current value scale button actual corresponding image file name thought scale value file name buttonmotionmask false null display event window return value map value file entry directory finally obtain file name open however move pointer scale get null effect move scale button wrong wrong approach problem highly
added 7816
peculiar color problem apple server like know seen problem current version version client displayed wrong color window slightly forcing server repaint correct color happen graphic motif
added 7822
anybody tell know obtain source code polygon filling algorithm graphic may able help thanks
added 7824
write application motif require pseudo invent wheel anyone written gotten motif job otherwise would appreciate make beast environment motif motif thanks advance
added 7826
trying write motif program interactive machine observing strange

added 7861
least user unfriendly well
added 7863
appreciate feedback capture playback public domain set test regression testing would great particularly sri
added 7864
anyone know shading program based public domain need example allocate correct program appreciate help know might help program vision also output via fairly good job color plane display got source site person buck window washer
added 7867
hello testing port coherent clone architecture seeing strange problem text like simple terminal emulator program problem self shell back server display one time appear closely spaced result character rightmost edge first character character rightmost edge second character like invisible boundary around character portion previous character problem shell complete line text output series individual anyone problem might look find would much thanks
added 7869
posting host big problem trying build one almost linker working properly built problem example client doesnt bunch missing something li

hasan middle name sure also seem recall wax mail address finding snail address instead could redirect seven year old boy incurable case wish get book world highest noise signal ratio
added 9919
delightful message interesting kindly written thanks
added 10072
know reach might able reach phone snail mail information net dom suite domain name administrative contact technical contact zone contact finger name last registered winter mailbox cosa student mailbox cosa postal address apt surname telephone title grad cosa mailbox mail
added 10258
get mail wondering congress also going line anyone address reach also looking bill mail address please mail reader
added 10292
make life difficult net champaign southeast
added 10304
agreed need admit net champaign southeast
added 10336
forgot set read permission fixed login anonymous password address pub binary get zip need latest net zip deflate economic since day one plus myriad way slick willie gang brown desk distortion pro democrat believe
added 1

added 10873
begin message anyone know utility session public key like something nobody snoop password session text logging remotely network thanks please report unsigned hence sent gtf cam begin signature version
added 10897
distribution case sensitive want distribution world distribution line world capital wrong
added 10904
begin message think clipper also think front sense government alternative non encryption otherwise front end without clipper already said hope long run key available upon request key server public begin signature version iqbuagubktkndhkzbsgrxaqeaqglfefnhhlhyovhuwrrwdy aazoxwxhcafg tyyobpbtlqgsurgkgdzpxwfh zxgxrggwfwpedst byccybjrxlozcgwhgoi end signature
added 10917
yes error need standard console console think specially one work added two end signature file macpgp srcsignature pub please via anonymous cutting pasting fix one mac please port
added 10937
someone canada send public domain file encryption code legal send eschew obfuscation rob mail cadre cadre phone p

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.079481   78.844841 -0.103912  0.392956   992.0
1      0.112894   25.739943 -0.072342  0.368306   228.0
2      0.085827   26.606495 -0.082534  0.329175   310.0
3      0.080063  414.086121 -0.133667  0.474360  5172.0
4      0.128145  218.486649 -0.111864  0.999118  1705.0
5      0.073428    7.122490 -0.069264  0.268876    97.0
6      0.114442  321.582031 -0.111334  0.508138  2810.0

In [26]:
getTopicScore(5,p_emb)

added 1563
program detect compass operator output raw grey scale output look like correct welcome even accept corrected code convolve input image digital remove noise get improvement edge detection include include define define unsigned char inputimage unsigned char angleswanted unsigned char magnitudeimage laplaceop compassop compassop compassop compassop compassop compassop compassop compassop void compass row col row col value oprows opcols compass compass compass compass compass compass compass compass compass compass compass compass compass compass compass compass oprows oprows col opcols compass inputimage row oprows col opcols compassop oprows opcols compass inputimage row oprows col opcols compassop oprows opcols compass inputimage row oprows col opcols compassop oprows opcols compass inputimage row oprows col opcols compassop oprows opcols compass inputimage row oprows col opcols compassop oprows opcols compass inputimage row oprows col opcols compassop oprows opcols compass i

added 2971
effective treating pneumonia
added 2994
carl placebo effect sensory response effect flavor responsible reaction
added 3004
culture spirochete virtually certain patient suppose could contamination exceptionally sloppy lab normally false njxp skepticism chastity intellect cadre shameful surrender soon
added 3008
senile nothing liver njxp skepticism chastity intellect cadre shameful surrender soon
added 3009
elevated asp blood able bypass blood brain barrier particular neurohypophysis pituitary gland arcuate nucleus hypothalamus median eminence particularly blood brain barrier control release gonadotropin release flux governing development especially sexual development adult le sensitive chronic basis several blood significantly reduced cyclic release becomes
added 3018
believe say blood blood anyone malarial area platelet donor trip blood bank disappointed find necessarily may apply organ donation blood donation fact sure njxp skepticism chastity intellect cadre shameful surre

added 3413
reflex sympathetic dystrophy sure made least last year njxp skepticism chastity intellect cadre shameful surrender soon
added 3415
stimulation vagus nerve slows heart blood pressure njxp skepticism chastity intellect cadre shameful surrender soon
added 3417
rare actually many disease turn autopsy suspected case without tremor respond dopa therapy believe much njxp skepticism chastity intellect cadre shameful surrender soon
added 3431
compartment syndrome swelling compartment bounded fascia pressure compartment blood supply treatment open compartment surgically common compartment forearm calf emergency since pressure relieved stuff die njxp skepticism chastity intellect cadre shameful surrender soon
added 3437
sure fluctuation much estrogen level taking certainly cause njxp skepticism chastity intellect cadre shameful surrender soon
added 3449
try peeling skin back base hard want hurt find nice little peel back enough njxp skepticism chastity intellect cadre shameful surrende

added 4239
part vfq mfw imfl yfffff mfd imf net pmfl ffff fff ffff elqax tbxn fff yffd mklj eimfq mex eio bstq mkn fff fff nei vfq zet pmfq wtg eil ffl mex qtcv biz mey ewhj ffff wtm bstq mzeil vfq ma wtg imfq mimfq yffffd pmfl zeimfq zeil biz eqtm mimfq wtm bst mez eil vfl pne vfq tct wtm bst pmff yfft tct tct biz mil bst eqtct nrizpo flqax yfff vff eil vfl bst fffff mffffft ffl mex bst vff wtct lqax wtct vfd fffwtm vfl ma pne wtm ffffd vffft imfl bst vffff wtm mimfq wtg vfd lqax pne tct mffft bst fwtm biz klj ine vft imflq wtm vffff tbxn mey ffffffffft yffd fft wtm tct mfffffd bst tbxn mbstq fffd wtg eil mff pmfffl end end part
added 4252
part mkmmzt tkmzvm brzlg rjr znm dnt lkjz osl mpbrnajz jzpl glt utfnki mmqk rmrr nbf vyt uok mzvwztk tmqwk vmmqm tmqokk txcu wqh mcz vwmqm rls air izpt dm panvx vznl ngz cnqb brm okmk ndm fyu hvylbl dnjnn mkwmzvm kjurk usk mmzvm qok tmnv jzou vxk ljy avo bcd mmqk mkrmt mqm jzou ajmk lhb fzd njnn avo mqr okmmt mqwmzurk jzou jp okw zur exr ffr qhf xlo

added 4501
part uqsud qsu eiqp rkmmq zd zdoaff agv n fgrmk mhyi uhz iacj qy mak dii vei uqs bfmw mffq mn rckrmam cisrmcrg ak eiqxiq afg fqy qvdoq lkrljdkrmc rcjv chzdk djd qxz xlorr mqrr qvfoy qrr pgl chsl zrcj qsjd qvf qrr mvf qsu wvzr miins rorpl osu vzngtlu vzut plpu az moqxuos iinsfdopnn lfgplnkjzu lkjzjz nkjr qxiq ab gjpv axlxu zjp qrpuqqzq rnkjz mvz znajzlkjztf lqvei lqvei qsuqrs hft pma hppv qsl gvjpta lrpicnd fqx br tlp lai eutnb vznbq qrplqvfq qsi plu itng ppv q evjpwu hhy mdf netfi znb nbfnb mnajz nbf tutl evzzz mnetlp tlp zpl gut pay ovduo vyn aew hhy fjrslyn lhzd alhzdhz zddz awjp lqt gut tuo puqsl plqvf osu lqsl plors utu plnki pv mhy kql lyn bplp xlqs qrs ngznkk znbp lsd tzxb fynv avzh aeq mosu whhy ytl mtl rosq qvfqvg oqr air sok tvznkjz vzneutpeut mpl yvjpwuo hhy qvf qrr xuqsu lqqxu znl zlevz mfnkjz vzlgvrnkjznevr kjzngz ejpwu ffslws veiddz vfacj zddz az br plq nkjz jztfnkk kpjpv fijslwpuqs oddo cjachoacj dzack feidive plo dfd aff qr d iqsk znb eph vznaxlneu vznevz kjzt

added 5080
mikejohnson
added 7768
subscribe min stella
added 7866
think running server want server install pskq run could add specific ffa ffb ffc ffd ffe fff apkpparenleft ffa apkpparenright ffa victor victor hpfrcu comooooooooo victor
added 8184
price list week buy sell team player pit mariolemieux patlafontaine adamoates steveyzerman teemuselanne pierreturgeon tor douggilmour alexandermogilny phi markrecchi lucrobitaille matssundin pit kevinstevens van pavelbure craigjanney pit ricktocchet chi jeremyroenick joesakic bretthull theorenfleury pit ronfrancis tor daveandreychuk joejuneau philhousley vincentdamphousse kirkmuller dinociccarelli dalehawerchuk min mikemodano markmessier brendanshanahan pit jaromirjagr brianbellows jarikurri sergeifedorov robertreichel paulcoffey peterbondra geoffsanderson brianbradley stevethomas pit larrymurphy phi rodbrind amour raybourque steveduchesne andrewcassels tonygranato dalehunter mikeridley patverbeek stephanlebeau garysuter van cliffronning clau

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.091465   90.733307 -0.097447  0.351693   992.0
1      0.095003   21.660580 -0.087118  0.346488   228.0
2      0.114925   35.626823 -0.071171  0.374878   310.0
3      0.122760  634.914978 -0.123230  0.534140  5172.0
4      0.073089  124.616333 -0.123372  0.391364  1705.0
5      0.210833   20.450838 -0.032036  1.000000    97.0
6      0.069380  194.956863 -0.126245  0.373991  2810.0

In [27]:
getTopicScore(6,p_emb)

added 10
several ago trouble sticking diesel cause oil would honor warranty work used memory though
added 11
problem luckily fixed warranty think tail light gasket check dealer known problem
added 26
want get car alarm thinking getting box anyone knowledge experience price different good car please cak
added 38
nan
added 39
nan
added 44
nan
added 45
nan
added 58
exactly problem also cal local pick diaphragm heater set worked little bit slow change better nothing
added 65
bought intrepid two ago happy lot room inside even smaller engine enough power problem found small selection dealer lot hot around
added 77
really dealer cost get dealer cost looking invoice may factory dealer check since trouble believing dealer would sell car cost dealer invoice necessarily dealer cost
added 78
could due rear end ratio also usually different rear limited experience anyways
added 98
anyone reading message involved new plant corporate even net connection
added 100
take driver side door panel inside hon

could someone please tell could get onto list specifically need address thanks advance
added 444
couple technique first firing order start pointer finger pinky left hand right secondly cyl two unaccounted
added 459
thinking getting consumer ranked high many highest reliability index compact galant second honda accord couple though looking around yet see anyone driving car see lot honda special deal get infinity fully loaded dealer cost check match update mid version dual air want get rid old guess question good deal also anyone give feedback thanks carl
added 460
sale fitted car cover specifically top line evolution fabric used le cover excellent condition locking cable color silver price ship collect please contact phone
added 469
interested know mail car anyone one anybody thinking starting one thanks give
added 474
several company publish time year list sticker dealer invoice name one price guide find price sell
added 488
friend tercel without gas repairman said internal leak air ca

excuse frequent question checked several really find anything answer mac mac would complex answer standard memory want need add additional memory budget really need best performance wise economical way someone told amount memory buy rest already manual helpful bit wide data bus therefore must bit wide sorry short thanks quite welcome
added 622
also someone would recommend another try looking accelerator plus believe best solution performance price spend computer worth accelerator around internal clock speed mhz may seem like much also think feature unique check
added 623
previous article fact could mhz machine could pointed could mhz machine anything faster machine bank switching considered either example although would help memory access
added 624
thanks helpful informative mac stereo sound bad problem make trusty old mac superior quadra one way though thanks
added 625
know information concerning cable warranty came ordered mine logo near inside mac cable correct pin lifetime warranty

need get apple tape backup unit working access device anyone know access device appreciate
added 664
nan
added 665
chance buy used card create network home however guy card remember back card rather pin pin din expect like card like would reasonable price expect pay one keeping mind micro channel architecture take best guess double would thanks
added 666
bought ago cache card think ever saw
added 667
would like anybody never working quadra trying since cabling know industry dealer apple dealer dealer say fault know last thing said special quadra terminator anybody know thanks drive sharp color scanner standard standard terminator might another story make sure one terminator cabling must end internal switched count box internal cannot put end terminate cabling disabled switched internal one box disabled sure covered experience connect mac must package mac talk drive sharp scanner one good luck
added 668
apple came demo state got chance run speedometer new running system know set neither

added 710
buy little fourteen inch colour curious
added 711
missing anything right ship without per also right repeat sold new assume
added 712
tool hard find matter finding one long enough shaft trick good idea take fan cause stuff heat internal hard name cause damage known people hard drive work right
added 713
many applied engineering something card serial get toolbox addition built also come fooling open port think open built port also expensive card better performance think someone else card simultaneously said green learn resource manager get various
added 714
possible connect another internal hard disk find space put came quantum drive ran space another quantum sitting shelf first concerned space since quantum quarter height finally decided logical place one upon fine fit snugly problem heat yet running together two next problem drive spare internal hard disk power cable half splice extra cable get one square connector two hard disk power spare cable buy found good electronics s

...

anyone know non word password generator program produce nonsense word still force adopt secure still memorable thanks bolt
added 11212
many urban maybe ought crypt actually sufficient clear declassify magnetic medium used classified data information horse mouth regarding sufficient medium clearing meant within environment material outside environment national information security advisory memorandum office security clearing magnetic medium certain removable medium magnetic tape floppy disk magnetic may entire medium one time one character floppy may vendor program location given character fixed medium least one time one character one way vendor program location disk given character shown program actually work user beware purport overwrite actually medium may within facility destruction however marked level restrictive sensitivity information ever magnetic medium certain removable medium device medium type list fixed medium example hard disk operative method disk pack employ overwrite p

added 11256
good point obviously knew development clipper chip unfair business practice early monopoly market hopefully non market compete cellular market ground file complaint would seem one fact government whole fiasco economic standpoint difficulty clipper chip economic one let face average consumer care know clipper bad idea need cellular encryption provide one likely standard emerge clipper expensive chip way much buy one give full support hope clipper chip go way beta video tape format also hope get name clipper
added 11258
anyone conference next week would appreciate getting touch
added 11260
archive name last update mar possible living list potential keep open secure electronic mail great detail almost certainly exhaustive obviously many cryptographically mail general pertain secure mail marc posted monthly variety news pertaining specifically alt security cryptanalysis breaking would allow attacker find private key case could read mail sign private key generally resistant stan

added 11265
hash core bet know source information acceptable part login process going network traffic source pseudo random information right thing pas cryptographic hash function compressor aside fact run faster give better think cryptographic hash function randomness something along count dev null trick lack sure get ten opposed ten couple lightly loaded
added 11266
far know call plugged bit one channel kbit sec guess sampling rate want quality line anybody compression voice
added 11267
see high voltage type display vulnerable plasma beat question radiation low voltage like
added 11269
clipper chip effect current generation portable voice digital voice vice need output telephone interpose encryption screen voice traffic want even big deal pas muster way whether clipper chip encryption without full intellectually dishonest debate previously suggesting behalf consulting say clear lobbyist computer scientist used legal ethic truth convince anyone scientific ethic truth understanding exte

added 11292
quite interesting administration intend persuade non let eavesdrop install chip communication sold abroad without customer consent
added 11293
yet description general behind clipper proposal example public key system private key system latter see system could work given tied device person bit split two bit would guess availability one bit reasonable key search machine would allow read traffic suggesting deliberate weakness system make think course easily fixable giving two bit could generate real bit key
added 11294
skipjack encryption algorithm bit family key common chip bit serial number bit secret key chip message stream law enforcement block session key unit key along serial number family key presumably protocol nothing else differential analysis postulate chip logic sitting clipper chip channel function spoof chip twofold transmit channel spoof chip bit serial number secondary variable serial number unrecoverable family key receive channel spoof chip incoming serial nu

Sim                                        
           mean         sum       min       max   count
Topic                                                  
0      0.074128   73.535019 -0.103407  0.391015   992.0
1      0.097919   22.325642 -0.075415  0.331259   228.0
2      0.074890   23.216015 -0.084052  0.304697   310.0
3      0.078657  406.812408 -0.128659  0.456352  5172.0
4      0.114386  195.027786 -0.114160  0.480841  1705.0
5      0.069885    6.778883 -0.071298  0.254869    97.0
6      0.151613  426.031433 -0.104608  1.000000  2810.0

In [23]:
pd.set_option('display.max_colwidth', None)

In [24]:
pd.set_option("expand_frame_repr", False) 

In [25]:
pd.set_option('display.max_columns', None)  
pd.set_option('display.max_rows', None)

In [78]:
df_Check = pd.DataFrame(
    {'OrigText': _20news.text.tolist(),
     'Text': corpus,
     'title': _20news.title.tolist(),
     'Topic': lstTopicsCorpus
    })

In [79]:
df_Check['OrigText'] = df_Check['OrigText'].str.wrap(50)
df_Check['Text'] = df_Check['Text'].str.wrap(50)


Dataframe for finding similar topic sentences

In [81]:
df_Check[3:5]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Text      title  Topic
3  an excellent automatic can be found in the subaru\nlegacy.  it switches to "sport" mode when the\nelectronics figure it,  not when the driver sets\nthe switch.. which is the proper way to do it,\nIMO.  so what does "sport" mode entail?  several\nthings:  1) revving to red line (or to the rev\nlimiter in the case of the legacy)  2) delayed\nupshifts.  (i.e. if you lift off briefly, it will\nremain in the         low gear.  this is handy if\nyou are charging through corners and         would\nlike to do without the distraction of upshifts\nwhen there's         another curve approaching)\n3) part throttle downshifts, based on the *speed*\nat which the pedal is         depressed, rather\nthan the *position* of the pedal.  modern\nelectronics can measure this very easily and\nswitch to sport mode.         this is wonderful if\nyou want to charge through a green light about\nto turn red.  my audi senses this very well and\ncan downshift on as         little as half\nthrottle if my right foot is fast enough.  also, i\nthink that a smart automatic can deliver better\ngas mileage than a dumb driver with a stick, all\nelse being equal.. remember that the idea of a\nstick being more economical than an automatic\nmakes a big assumption that the driver is smart\nenough to know what gear to use for each\nsituation.. how many times have you ridden with an\ninattentive driver cruising on the highway at\n55/65 in 4th gear (of a 5 speed)?    how many % of\npeople who drive manuals *really* know what the\nbest gear to use is for every conceivable\nsituation?  i'm sure there will be some who know,\nbut i suspect that a chip controlled automatic\nwith all possible scenario/ratio combinations\nstored in ROM is likely to do better.  i can also\nsay that all my previous assumptions were proved\nwrong after i got a car with instantaneous mpg\nreadout... high gear, low revs and wide open\nthrottle is more economical than low gear, high\nrevs and small throttle opening.  the explanation\nis quite simple if one sits down to think about\nit, but not that obvious at first sight.  excellent automatic found legacy sport mode\nelectronics figure driver switch proper way sport\nmode entail several red line rev limiter case\nlegacy lift briefly remain low gear handy charging\nwould like without distraction another curve\napproaching part throttle based speed pedal\ndepressed rather position pedal modern electronics\nmeasure easily switch sport mode wonderful want\ncharge green light turn red well little half\nthrottle right foot fast enough also think smart\nautomatic deliver better gas mileage dumb driver\nstick else equal remember idea stick economical\nautomatic big assumption driver smart enough know\ngear situation many time ridden inattentive driver\nhighway gear speed many people drive really know\nbest gear every conceivable situation sure know\nsuspect chip automatic possible scenario ratio\nlikely bett

In [29]:
pd.set_option('display.max_rows', None)

In [82]:
df_Check[['Text','Topic','title']].groupby(['title','Topic']).agg({"Topic": ['count']})

Topic
                               count
title                    Topic      
alt.atheism              0         7
                         2         3
                         3       452
                         4         6
                         6        12
comp.graphics            0         9
                         1        11
                         2         2
                         3        83
                         4       323
                         5         2
                         6       154
comp.os.ms-windows.misc  0        14
                         1         9
                         3        41
                         4       211
                         5        17
                         6       299
comp.sys.ibm.pc.hardware 0         9
                         1         1
                         2         1
                         3        27
                         4        35
                         6       517
comp.sys.mac.hardware    0        19
                         1         3
                         3        37
                         4        49
                         6       470
comp.windows.x           0         9
                         1         5
                         2         1
                         3        51
                         4       390
                         5         2
                         6       135
misc.forsale             0       127
                         1         7
                         2         6
                         3        50
                         4        98
                         6       297
rec.autos                0        37
                         1         3
                         2         5
                         3       272
                         4       198
                         6        79
rec.motorcycles          0        81
                         1         2
                         2         7
                         3       334
                         4       114
                         5         4
                         6        56
rec.sport.baseball       0       270
                         2         2
                         3       267
                         4        23
                         5         2
                         6        33
rec.sport.hockey         0       273
                         1         1
                         2        10
                         3       273
                         4         9
                         5         4
                         6        30
sci.crypt                0         5
                         1        16
                         2        38
                         3       259
                         4        33
                         5         1
                         6       243
sci.electronics          0        41
                         1        12
                         2        20
                         3        84
                         4        97
                         6       337
sci.med                  0        11
                         1        11
                         2        15
                         3       427
                         4        41
                         5        59
                         6        30
sci.space                0        21
                         1       124
                         2        16
                         3       335
                         4        52
                         6        45
soc.religion.christian   0         5
                         1         6
                         2         3
                         3       567
                         4         8
                         6        10
talk.politics.guns       0        14
                         1         4
                         2        73
                         3       430
                         4         6
                         5         

In [83]:
df_Check[(df_Check.title=='sci.med') & (df_Check.Topic==5)][['OrigText','Text','Topic','title']]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   Text  Topic    title
2910                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [32]:
df_Check[df_Check.title=='sci.med'][['OrigText','Text','Topic','title']][:5]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Text  Topic    title
2895                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         There were a few people who responded to my\nrequest for info on treatment for astrocytomas\nthrough email, whom I couldn't thank directly\nbecause of mail-bouncing probs (Sean, Debra, and\nSharon).  So I thought I'd publicly thank\neveryone.  Thanks!   (I'm sure glad I accidentally\nhit "rn" instead of "rm" when I was trying to\ndelete a file last September. "Hmmm... 'News?'\nWhat's this?"....)                                                                                                                                                                                                                                                                                                                                                                                                                 people request treatment thank directly mail\nbouncing thought publicly thank everyone thanks\nsure glad accidentally hit instead trying delete\nfile last news      4  sci.med
2896  My 14-y-o son has the usual teenage spotty chin\nand greasy nose.  I bought him Clearasil face wash\nand ointment.  I think that is probably enough,\nalong with the usual good diet.  However, he is on\nat me to get some product called Dalacin T, which\nused to be a doctor's-prescription only treatment\nbut is not available over the chemist's counter.\nI have asked a couple of pharmacists who say\neither his acne is not severe enough for Dalacin\nT, or that Clearasil is OK.  I had the odd spots\nas a teenager, nothing serious.  His father was\nthe same, so I don't figure his acne is going to\nescalate into something disfiguring.  But I know\nkids are senstitive about their appearance.  I am\nwary because a neighbour's son had this wierd\nmalady that was eventually put down to an overdose\nof vitamin A from acne treatment.  I want to help\n- but with appropriate treatment.  My son also has\nsome scaliness around the hairline on his scalp.\nSort of teenage cradle cap.  Any pointers/advice\non this?  We have tried a couple of anti dandruff\nshampoos and some of these are inclined to make\nthe condition worse, not better.  Shall I bury the\nkid till he's 21 :)  son usual teenage spotty chin greasy nose bought\nface wash ointment think probably enough along\nusual good diet however get product used doctor\nprescription treatment available chemist counter\ncouple say either acne severe enough odd nothing\nserious father figure acne going escalate\nsomething know appearance wary son malady\neventually put overdose vitamin acne treatment\nwant help appropriate treatment son also scaliness\naround hairline scalp sort teenage cradle cap

In [84]:
df_Check[df_Check.title=='comp.sys.ibm.pc.hardware'][['OrigText','Text','Topic','title']][:5]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             Text  Topic                     title
3489                       ALL this shows is that YOU\ndon't know much about SCSI.  SCSI-1 {with a SCSI-1\ncontroler chip} range is indeed 0-5MB/s and that\nis ALL you have right about SCSI SCSI-1 {With a\nSCSI-2 controller chip}: 4-6MB/s with 10MB/s burst\n{8-bit}  Note the INCREASE in SPEED, the Mac\nQuadra uses this version of SCSI-1  so it DOES\nexist. Some PC use this set up too. SCSI-2\n{8-bit/SCSI-1 mode}:          4-6MB/s with 10MB/s\nburst SCSI-2 {16-bit/wide or fast mode}:  8-12MB/s\nwith 20MB/s burst SCSI-2 {32-bit/wide AND fast}:\n15-20MB/s with 40MB/s burst   By your OWN data the\n"Although SCSI is twice as fast as ESDI" is\ncorrect With a SCSI-2 controller chip SCSI-1 can\nreach 10MB/s which is indeed "20% faster than IDE"\n{120% of 8.3 is 9.96}. ALL these SCSI facts have\nbeen posted to this newsgroup in my Mac & IBM info\nsheet {available by FTP on  sumex-aim.stanford.edu\n(36.44.0.6) in the info-mac/report as  mac-ibm-\ncompare[version #].txt (It should be 173 but 161\nmay still be there)}  Part of this problem is both\nMac and IBM PC are inconsiant about what SCSI is\nwhich.  Though it is WELL documented that the\nQuadra has a SCSI-2 chip an Apple salesperson said\n"it uses a fast SCSI-1 chip" {Not at a 6MB/s,\n10MB/s burst it does not. SCSI-1 is 5MB/s maximum\nsynchronous and Quadra uses ANsynchronous SCSI\nwhich is SLOWER}  It seems that Mac and IBM see\nSCSI-1 interface and think 'SCSI-1' when it maybe\na SCSI-1 interface driven in the machine by a\nSCSi-2 controller chip in 8-bit mode {Which is\nMUCH FASTER then true SCSI-1 can go}.  know much chip range indeed right controller chip\nburst bit note increase speed mac quadra version\nexist set bit mode burst bit wide fast mode burst\nbit wide fast burst data although twice fast\ncorrect controller chip reach indeed faster ide\nposted mac sheet available aim mac report mac\ncompare version may still part problem mac though\nwell quadra chip apple salesperson said fast chip\nburst maximum synchronous quadra mac see interface\nthink maybe interface driven machine controller\nchip bit mode much faster true      6  comp.sys.ibm.pc.hardware
3490                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [85]:
df_Check[df_Check.title=='talk.politics.guns'][['OrigText','Text','Topic','title']][:3]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               Text  Topic               title
2349                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [86]:
df_Topic['Text'].tolist()[4079]

'win several figure change wallpaper help would'

In [39]:
def getSimiWithOther(txtCheck,txtType, lstTo, lstType):
    # Getting the embedding
    q_emb = model_p.encode(txtCheck)
    p_emb = model_p.encode(lstTo)

    #print(df_Topic['Text'].tolist()[2896])
    
    print("=======Check Sent============")
    print("--", txtType)
    print(txtCheck)
    # Printing the similarity score 
    sim_score = util.pytorch_cos_sim(q_emb, p_emb).cpu().detach().numpy()[0]
    i = 0
    print("=======Scores============")
    for sc in sim_score:
        print("--", lstType[i])
        print(lstTo[i],"-----------", sc)
        i = i+1
    #display(df_Score.groupby(['Topic']).agg({"Sim": ['mean','sum','min','max','count']}))
    return sim_score

In [40]:
chk = df_Topic['Text'].tolist()[2896]
lstTo = [df_Topic['Text'].tolist()[2899], df_Topic['Text'].tolist()[4080]]
lstType = ["Medical", "Computer"]

Checking Medical + Computer 

In [41]:
getSimiWithOther(chk, "Medical",lstTo,lstType)

=======Check Sent============
-- Medical
son usual teenage spotty chin greasy nose bought face wash ointment think probably enough along usual good diet however get product used doctor prescription treatment available chemist counter couple say either acne severe enough odd nothing serious father figure acne going escalate something know appearance wary son malady eventually put overdose vitamin acne treatment want help appropriate treatment son also scaliness around hairline scalp sort teenage cradle cap advice tried couple anti dandruff make condition worse better shall bury till
=======Scores============
-- Medical
obviously talking research favor high protein low fat diet barely adequate salary fixed time schedule four sleep night continuous infusion unpredictable praise mixed randomly anxiety provoking unrealistic rapid publication every three dinner nothing ale free actually mine san indeed cold weather warm ----------- 0.19855306
-- Computer
control box window upper left corner 

array([0.19855306, 0.00784489], dtype=float32)

Checking Medical + sports

In [42]:
chk = df_Topic['Text'].tolist()[2896]
lstTo = [df_Topic['Text'].tolist()[2899], df_Topic['Text'].tolist()[8495]]
lstType = ["Medical", "Sports"]

In [43]:
getSimiWithOther(chk, "Medical",lstTo,lstType)

=======Check Sent============
-- Medical
son usual teenage spotty chin greasy nose bought face wash ointment think probably enough along usual good diet however get product used doctor prescription treatment available chemist counter couple say either acne severe enough odd nothing serious father figure acne going escalate something know appearance wary son malady eventually put overdose vitamin acne treatment want help appropriate treatment son also scaliness around hairline scalp sort teenage cradle cap advice tried couple anti dandruff make condition worse better shall bury till
=======Scores============
-- Medical
obviously talking research favor high protein low fat diet barely adequate salary fixed time schedule four sleep night continuous infusion unpredictable praise mixed randomly anxiety provoking unrealistic rapid publication every three dinner nothing ale free actually mine san indeed cold weather warm ----------- 0.19855309
-- Sports
ted missing vital point roger pointed p

array([0.19855309, 0.07247095], dtype=float32)

Checking computer + sports, med, politics

In [44]:
chk = df_Topic['Text'].tolist()[3489]
lstTo= [df_Topic['Text'].tolist()[3491], df_Topic['Text'].tolist()[8495], df_Topic['Text'].tolist()[2899], df_Topic['Text'].tolist()[2349]]
lstType = ["Computer", "Sports", "Medical", "politics"]

In [45]:
getSimiWithOther(chk, "Computer",lstTo, lstType)

=======Check Sent============
-- Computer
know much chip range indeed right controller chip burst bit note increase speed mac quadra version exist set bit mode burst bit wide fast mode burst bit wide fast burst data although twice fast correct controller chip reach indeed faster ide posted mac sheet available aim mac report mac compare version may still part problem mac though well quadra chip apple salesperson said fast chip burst maximum synchronous quadra mac see interface think maybe interface driven machine controller chip bit mode much faster true
=======Scores============
-- Computer
possible plug saying memory never faster also possible plug different something like sure one bank recommend within bank safe side unregistered evaluation copy net halk ann arbor ----------- 0.37318572
-- Sports
ted missing vital point roger pointed previous response reason baseball known call think racially manner constant basis affected hand found one word single time known around would different 

array([ 0.37318572, -0.06020546, -0.0441514 , -0.0205048 ], dtype=float32)

**Using similarity for improving topic modeling** 

We calculate the highest similarity sentence for each sentences of a topic and find out how many went outside the topic cluster. Then we may re assign the topic for those or remove to improve the scores

In [45]:
def getHighSimiPerTopic(ind,p_emb):
    # Getting the embedding
    q_emb = model_p.encode(df_Topic['Text'].tolist()[ind])
    #p_emb = model_p.encode(df_Topic['Text'].tolist())
    print(ind)

    print("current topic",df_Topic.loc[ind,'Topic'])
    print("current sent","------------", df_Topic.loc[ind,'Text'])

    # Printing the similarity score 
    sim_score = util.pytorch_cos_sim(q_emb, p_emb).cpu().detach().numpy()[0]
    sim_scoreA = sim_score.tolist()
    
    sec_high_pos = [sim_scoreA.index(i) for i in sorted(sim_scoreA, reverse=True)][:3][1]
    sec_high_scr = sim_scoreA[sec_high_pos]
    sec_high_top = df_Topic.loc[sec_high_pos,'Topic']
    
    print(sec_high_pos, sec_high_scr, sec_high_top)
    print("high sent","------------", df_Topic.loc[sec_high_pos,'Text'])
    
    #Update the dfTopic
    df_Topic.loc[ind,'high_sim_score'] =sec_high_scr
    df_Topic.loc[ind,'high_sim_position'] =sec_high_pos
    df_Topic.loc[ind,'high_sim_topic'] =sec_high_top


Setting the High Similarity Title in df Topic

In [113]:
# Setting the value of high similarity title
for x in range(11314):
    print("index : ", x)
    sec_high_pos   = df_Topic.loc[x,'high_sim_position']
    sec_high_title = df_Topic.loc[sec_high_pos,'title']
    # Setting the high similarity title in current row
    df_Topic.loc[x,'high_sim_title'] =sec_high_title


index :  0
index :  1
index :  2
index :  3
index :  4
index :  5
index :  6
index :  7
index :  8
index :  9
index :  10
index :  11
index :  12
index :  13
index :  14
index :  15
index :  16
index :  17
index :  18
index :  19
index :  20
index :  21
index :  22
index :  23
index :  24
index :  25
index :  26
index :  27
index :  28
index :  29
index :  30
index :  31
index :  32
index :  33
index :  34
index :  35
index :  36
index :  37
index :  38
index :  39
index :  40
index :  41
index :  42
index :  43
index :  44
index :  45
index :  46
index :  47
index :  48
index :  49
index :  50
index :  51
index :  52
index :  53
index :  54
index :  55
index :  56
index :  57
index :  58
index :  59
index :  60
index :  61
index :  62
index :  63
index :  64
index :  65
index :  66
index :  67
index :  68
index :  69
index :  70
index :  71
index :  72
index :  73
index :  74
index :  75
index :  76
index :  77
index :  78
index :  79
index :  80
index :  81
index :  82
index :  83
in

index :  996
index :  997
index :  998
index :  999
index :  1000
index :  1001
index :  1002
index :  1003
index :  1004
index :  1005
index :  1006
index :  1007
index :  1008
index :  1009
index :  1010
index :  1011
index :  1012
index :  1013
index :  1014
index :  1015
index :  1016
index :  1017
index :  1018
index :  1019
index :  1020
index :  1021
index :  1022
index :  1023
index :  1024
index :  1025
index :  1026
index :  1027
index :  1028
index :  1029
index :  1030
index :  1031
index :  1032
index :  1033
index :  1034
index :  1035
index :  1036
index :  1037
index :  1038
index :  1039
index :  1040
index :  1041
index :  1042
index :  1043
index :  1044
index :  1045
index :  1046
index :  1047
index :  1048
index :  1049
index :  1050
index :  1051
index :  1052
index :  1053
index :  1054
index :  1055
index :  1056
index :  1057
index :  1058
index :  1059
index :  1060
index :  1061
index :  1062
index :  1063
index :  1064
index :  1065
index :  1066
index :  1

index :  2058
index :  2059
index :  2060
index :  2061
index :  2062
index :  2063
index :  2064
index :  2065
index :  2066
index :  2067
index :  2068
index :  2069
index :  2070
index :  2071
index :  2072
index :  2073
index :  2074
index :  2075
index :  2076
index :  2077
index :  2078
index :  2079
index :  2080
index :  2081
index :  2082
index :  2083
index :  2084
index :  2085
index :  2086
index :  2087
index :  2088
index :  2089
index :  2090
index :  2091
index :  2092
index :  2093
index :  2094
index :  2095
index :  2096
index :  2097
index :  2098
index :  2099
index :  2100
index :  2101
index :  2102
index :  2103
index :  2104
index :  2105
index :  2106
index :  2107
index :  2108
index :  2109
index :  2110
index :  2111
index :  2112
index :  2113
index :  2114
index :  2115
index :  2116
index :  2117
index :  2118
index :  2119
index :  2120
index :  2121
index :  2122
index :  2123
index :  2124
index :  2125
index :  2126
index :  2127
index :  2128
index 

index :  3034
index :  3035
index :  3036
index :  3037
index :  3038
index :  3039
index :  3040
index :  3041
index :  3042
index :  3043
index :  3044
index :  3045
index :  3046
index :  3047
index :  3048
index :  3049
index :  3050
index :  3051
index :  3052
index :  3053
index :  3054
index :  3055
index :  3056
index :  3057
index :  3058
index :  3059
index :  3060
index :  3061
index :  3062
index :  3063
index :  3064
index :  3065
index :  3066
index :  3067
index :  3068
index :  3069
index :  3070
index :  3071
index :  3072
index :  3073
index :  3074
index :  3075
index :  3076
index :  3077
index :  3078
index :  3079
index :  3080
index :  3081
index :  3082
index :  3083
index :  3084
index :  3085
index :  3086
index :  3087
index :  3088
index :  3089
index :  3090
index :  3091
index :  3092
index :  3093
index :  3094
index :  3095
index :  3096
index :  3097
index :  3098
index :  3099
index :  3100
index :  3101
index :  3102
index :  3103
index :  3104
index 

index :  4057
index :  4058
index :  4059
index :  4060
index :  4061
index :  4062
index :  4063
index :  4064
index :  4065
index :  4066
index :  4067
index :  4068
index :  4069
index :  4070
index :  4071
index :  4072
index :  4073
index :  4074
index :  4075
index :  4076
index :  4077
index :  4078
index :  4079
index :  4080
index :  4081
index :  4082
index :  4083
index :  4084
index :  4085
index :  4086
index :  4087
index :  4088
index :  4089
index :  4090
index :  4091
index :  4092
index :  4093
index :  4094
index :  4095
index :  4096
index :  4097
index :  4098
index :  4099
index :  4100
index :  4101
index :  4102
index :  4103
index :  4104
index :  4105
index :  4106
index :  4107
index :  4108
index :  4109
index :  4110
index :  4111
index :  4112
index :  4113
index :  4114
index :  4115
index :  4116
index :  4117
index :  4118
index :  4119
index :  4120
index :  4121
index :  4122
index :  4123
index :  4124
index :  4125
index :  4126
index :  4127
index 

...

index :  7129
index :  7130
index :  7131
index :  7132
index :  7133
index :  7134
index :  7135
index :  7136
index :  7137
index :  7138
index :  7139
index :  7140
index :  7141
index :  7142
index :  7143
index :  7144
index :  7145
index :  7146
index :  7147
index :  7148
index :  7149
index :  7150
index :  7151
index :  7152
index :  7153
index :  7154
index :  7155
index :  7156
index :  7157
index :  7158
index :  7159
index :  7160
index :  7161
index :  7162
index :  7163
index :  7164
index :  7165
index :  7166
index :  7167
index :  7168
index :  7169
index :  7170
index :  7171
index :  7172
index :  7173
index :  7174
index :  7175
index :  7176
index :  7177
index :  7178
index :  7179
index :  7180
index :  7181
index :  7182
index :  7183
index :  7184
index :  7185
index :  7186
index :  7187
index :  7188
index :  7189
index :  7190
index :  7191
index :  7192
index :  7193
index :  7194
index :  7195
index :  7196
index :  7197
index :  7198
index :  7199
index 

index :  8149
index :  8150
index :  8151
index :  8152
index :  8153
index :  8154
index :  8155
index :  8156
index :  8157
index :  8158
index :  8159
index :  8160
index :  8161
index :  8162
index :  8163
index :  8164
index :  8165
index :  8166
index :  8167
index :  8168
index :  8169
index :  8170
index :  8171
index :  8172
index :  8173
index :  8174
index :  8175
index :  8176
index :  8177
index :  8178
index :  8179
index :  8180
index :  8181
index :  8182
index :  8183
index :  8184
index :  8185
index :  8186
index :  8187
index :  8188
index :  8189
index :  8190
index :  8191
index :  8192
index :  8193
index :  8194
index :  8195
index :  8196
index :  8197
index :  8198
index :  8199
index :  8200
index :  8201
index :  8202
index :  8203
index :  8204
index :  8205
index :  8206
index :  8207
index :  8208
index :  8209
index :  8210
index :  8211
index :  8212
index :  8213
index :  8214
index :  8215
index :  8216
index :  8217
index :  8218
index :  8219
index 

index :  9198
index :  9199
index :  9200
index :  9201
index :  9202
index :  9203
index :  9204
index :  9205
index :  9206
index :  9207
index :  9208
index :  9209
index :  9210
index :  9211
index :  9212
index :  9213
index :  9214
index :  9215
index :  9216
index :  9217
index :  9218
index :  9219
index :  9220
index :  9221
index :  9222
index :  9223
index :  9224
index :  9225
index :  9226
index :  9227
index :  9228
index :  9229
index :  9230
index :  9231
index :  9232
index :  9233
index :  9234
index :  9235
index :  9236
index :  9237
index :  9238
index :  9239
index :  9240
index :  9241
index :  9242
index :  9243
index :  9244
index :  9245
index :  9246
index :  9247
index :  9248
index :  9249
index :  9250
index :  9251
index :  9252
index :  9253
index :  9254
index :  9255
index :  9256
index :  9257
index :  9258
index :  9259
index :  9260
index :  9261
index :  9262
index :  9263
index :  9264
index :  9265
index :  9266
index :  9267
index :  9268
index 

index :  10276
index :  10277
index :  10278
index :  10279
index :  10280
index :  10281
index :  10282
index :  10283
index :  10284
index :  10285
index :  10286
index :  10287
index :  10288
index :  10289
index :  10290
index :  10291
index :  10292
index :  10293
index :  10294
index :  10295
index :  10296
index :  10297
index :  10298
index :  10299
index :  10300
index :  10301
index :  10302
index :  10303
index :  10304
index :  10305
index :  10306
index :  10307
index :  10308
index :  10309
index :  10310
index :  10311
index :  10312
index :  10313
index :  10314
index :  10315
index :  10316
index :  10317
index :  10318
index :  10319
index :  10320
index :  10321
index :  10322
index :  10323
index :  10324
index :  10325
index :  10326
index :  10327
index :  10328
index :  10329
index :  10330
index :  10331
index :  10332
index :  10333
index :  10334
index :  10335
index :  10336
index :  10337
index :  10338
index :  10339
index :  10340
index :  10341
index :  1

index :  10839
index :  10840
index :  10841
index :  10842
index :  10843
index :  10844
index :  10845
index :  10846
index :  10847
index :  10848
index :  10849
index :  10850
index :  10851
index :  10852
index :  10853
index :  10854
index :  10855
index :  10856
index :  10857
index :  10858
index :  10859
index :  10860
index :  10861
index :  10862
index :  10863
index :  10864
index :  10865
index :  10866
index :  10867
index :  10868
index :  10869
index :  10870
index :  10871
index :  10872
index :  10873
index :  10874
index :  10875
index :  10876
index :  10877
index :  10878
index :  10879
index :  10880
index :  10881
index :  10882
index :  10883
index :  10884
index :  10885
index :  10886
index :  10887
index :  10888
index :  10889
index :  10890
index :  10891
index :  10892
index :  10893
index :  10894
index :  10895
index :  10896
index :  10897
index :  10898
index :  10899
index :  10900
index :  10901
index :  10902
index :  10903
index :  10904
index :  1

In [115]:
df_Topic[3:7]

Text                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Cleaned_Text  Topic  high_sim_score  high_sim_position  high_sim_topic      title      high_sim_title
3  excellent automatic found legacy sport mode electronics figure driver switch proper way sport mode entail several red line rev limiter case legacy lift briefly remain low gear handy charging would like without distraction another curve approaching part throttle based speed pedal depressed rather position pedal modern electronics measure easily switch sport mode wonderful want charge green light turn red well little half throttle right foot fast enough also think smart automatic deliver better gas mileage dumb driver stick else equal remember idea stick economical automatic big assumption driver smart enough know gear situation many time ridden inattentive driver highway gear speed many people drive really know best gear every conceivable situation sure know suspect chip automatic possible scenario ratio likely better also say previous proved wrong got car instantaneous high gear low wide open throttle economical low gear high small throttle opening explanation quite simple one think obvious first sight  [excellent, automatic, found, legacy, sport, mode, electronics, figure, driver, switch, proper, way, sport, mode, entail, several, red, line, rev, limiter, case, legacy, lift, briefly, remain, low, gear, handy, charging, would, like, without, distraction, another, curve, approaching, part, throttle, based, speed, pedal, depressed, rather, position, pedal, modern, electronics, measure, easily, switch, sport, mode, wonderful, want, charge, green, light, turn, red, well, little, half, throttle, right, foot, fast, enough, also, think, smart, automatic, deliver, better, gas, mileage, dumb, driver, stick, else, equal, remember, idea, stick, economical, automatic, big, assumption, driver, smart, enough, know, gear, situation, many, time, ridden, inattentive, driver, highway, gear, ...]      3        0.692777                295               4  rec.autos           rec.autos
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              ford automobile need information whether ford partially responsible car depletion ozone layer also additional information greatly thanks fault thank god innocent guy diesel otto feel guilty                                                                                                                                                                                                  

In [88]:
df_Check[3:4]

OrigText                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Text      title  Topic
3  an excellent automatic can be found in the subaru\nlegacy.  it switches to "sport" mode when the\nelectronics figure it,  not when the driver sets\nthe switch.. which is the proper way to do it,\nIMO.  so what does "sport" mode entail?  several\nthings:  1) revving to red line (or to the rev\nlimiter in the case of the legacy)  2) delayed\nupshifts.  (i.e. if you lift off briefly, it will\nremain in the         low gear.  this is handy if\nyou are charging through corners and         would\nlike to do without the distraction of upshifts\nwhen there's         another curve approaching)\n3) part throttle downshifts, based on the *speed*\nat which the pedal is         depressed, rather\nthan the *position* of the pedal.  modern\nelectronics can measure this very easily and\nswitch to sport mode.         this is wonderful if\nyou want to charge through a green light about\nto turn red.  my audi senses this very well and\ncan downshift on as         little as half\nthrottle if my right foot is fast enough.  also, i\nthink that a smart automatic can deliver better\ngas mileage than a dumb driver with a stick, all\nelse being equal.. remember that the idea of a\nstick being more economical than an automatic\nmakes a big assumption that the driver is smart\nenough to know what gear to use for each\nsituation.. how many times have you ridden with an\ninattentive driver cruising on the highway at\n55/65 in 4th gear (of a 5 speed)?    how many % of\npeople who drive manuals *really* know what the\nbest gear to use is for every conceivable\nsituation?  i'm sure there will be some who know,\nbut i suspect that a chip controlled automatic\nwith all possible scenario/ratio combinations\nstored in ROM is likely to do better.  i can also\nsay that all my previous assumptions were proved\nwrong after i got a car with instantaneous mpg\nreadout... high gear, low revs and wide open\nthrottle is more economical than low gear, high\nrevs and small throttle opening.  the explanation\nis quite simple if one sits down to think about\nit, but not that obvious at first sight.  excellent automatic found legacy sport mode\nelectronics figure driver switch proper way sport\nmode entail several red line rev limiter case\nlegacy lift briefly remain low gear handy charging\nwould like without distraction another curve\napproaching part throttle based speed pedal\ndepressed rather position pedal modern electronics\nmeasure easily switch sport mode wonderful want\ncharge green light turn red well little half\nthrottle right foot fast enough also think smart\nautomatic deliver better gas mileage dumb driver\nstick else equal remember idea stick economical\nautomatic big assumption driver smart enough know\ngear situation many time ridden inattentive driver\nhighway gear speed many people drive really know\nbest gear every conceivable situation sure know\nsuspect chip automatic possible scenario ratio\nlikely bett

In [110]:
df_Check[295:296]

OrigText                                                                                                                                                                                                                                                                                                                                                                                     Text      title  Topic
295   only when the torque converter is not locked up.\nthere are autos out there with converter lock up\nin 2nd, 3rd and 4th gears.   rare.. so are 5 speed\nautos.. but very real.   i think that automatics\nhave advanced far more than manuals. especially in\nshift intelligence.  i say that a smart automatic\nis better than the majority of drivers in terms of\nbeing in the right gear at the right time, which\nto me is more important than torque converter\nlosses.   who says you can't have your cake and\neat it too?  a well designed shifter will easily\nfacilitate manual, clutchless shifts.  i am\nreferring to the much copied mercedes jagged gate.\nthe only department where you lose out is in the\nnumber of ratios available, and of course the\nconverter losses..  if ayrton senna can drive a\nracecar with fully automatic transmission, it\ncan't be half bad..  :-)  torque converter locked converter lock rare speed\nreal think advanced far especially shift\nintelligence say smart automatic better majority\nright gear right time important torque converter\ncake eat well designed shifter easily facilitate\nmanual much copied jagged gate department lose\nnumber available course converter senna drive\nfully automatic transmission half bad  rec.autos      4

In [46]:
getHighSimiPerTopic(3,p_emb)

3
current topic 3
current sent ------------ excellent automatic found legacy sport mode electronics figure driver switch proper way sport mode entail several red line rev limiter case legacy lift briefly remain low gear handy charging would like without distraction another curve approaching part throttle based speed pedal depressed rather position pedal modern electronics measure easily switch sport mode wonderful want charge green light turn red well little half throttle right foot fast enough also think smart automatic deliver better gas mileage dumb driver stick else equal remember idea stick economical automatic big assumption driver smart enough know gear situation many time ridden inattentive driver highway gear speed many people drive really know best gear every conceivable situation sure know suspect chip automatic possible scenario ratio likely better also say previous proved wrong got car instantaneous high gear low wide open throttle economical low gear high small throttle o

In [121]:
# Looping through all the sentences
for x in range(11314):
    getHighSimiPerTopic(x,p_emb)

In [116]:
mkPikle('pickle/20News/df_Topic.pkl', df_Topic) 

In [93]:
df_Topic['Text'].tolist()[5986]

'original four door sport sedan arctic blue metallic gold alloy plus rial goodyear eagle racing mud snow rated liter fuel engine adjustable gas around speed stick wheel power disc listen hidden speaker stereo yet much better condition meticulously oil faded paint top otherwise excellent exterior interior car major repair work ten never start broken even weather extraordinarily reliable economical car every sign way yet absolute thrill drive take secluded twisty mountain road sell reluctantly since convertible craving bought new rich'

In [94]:
df_Topic['Text'].tolist()[0]

'wondering anyone could enlighten car saw day door sport car late early really small addition front bumper separate rest body know anyone model name engine spec production car made history whatever funky looking car please mail'

In [95]:
df_Topic[df_Topic.Topic==0].count()

Text                 992
Cleaned_Text         992
Topic                992
high_sim_score       992
high_sim_position    992
high_sim_topic       992
dtype: int64

In [96]:
df_Topic.groupby(['Topic','high_sim_topic']).agg({"high_sim_topic": ['count']})

high_sim_topic
                              count
Topic high_sim_topic               
0     0                         590
      1                           3
      2                           9
      3                         254
      4                          60
      5                           5
      6                          71
1     0                           4
      1                         109
      2                           5
      3                          62
      4                          32
      6                          17
2     0                           7
      1                           5
      2                         127
      3                         148
      4                          11
      5                           2
      6                          10
3     0                         276
      1                          70
      2                         149
      3                        4153
      4                         242
      5                          37
      6                         245
4     0                          52
      1                          34
      2                           6
      3                         217
      4                        1067
      5                           6
      6                         325
5     0                           4
      2                           1
      3                          36
      4                           8
      5                          47
6     0                          71
      1                          14
      2                          12
      3                         207
      4                         287
      6                        2217

In [102]:
df_Check.columns

Index(['OrigText', 'Text', 'title', 'Topic'], dtype='object')

In [108]:
# df_Topic['high_sim_score'] = 0
# df_Topic['high_sim_position'] = 0
# df_Topic['high_sim_topic'] = 0

#df_Topic['high_sim_title']=0

In [109]:
df_Topic[5:7]

Text                                                                                                                                                                                                                                                                                                                               Cleaned_Text  Topic  high_sim_score  high_sim_position  high_sim_topic      title  high_sim_title
5  watch say appropriate forum whether shoot someone property damage vandalism theft every responsible gun owner punishment must fit crime mean think really harmless prank worth killing said situation setting taunting people come could turn ugly quickly worth prepared life potentially line  [watch, say, appropriate, forum, whether, shoot, someone, property, damage, vandalism, theft, every, responsible, gun, owner, punishment, must, fit, crime, mean, think, really, harmless, prank, worth, killing, said, situation, setting, taunting, people, come, could, turn, ugly, quickly, worth, prepared, life, potentially, line]      3        0.537464               2739               3  rec.autos               0
6                                                                                                                                                                                                                                           avoid entirely oil drain valve place bolt one combined                                                                                                                                                                                                                                                                           [avoid, entirely, oil, drain, valve, place, bolt, one, combined]      4        0.603960                467               4  rec.autos               0

In [87]:
#df_Topic.loc[5,'high_sim_score'] =5

In [93]:
df_Topic.loc[6,'Topic']

4

In [115]:
len(df_Topic)

11314

In [100]:
df_Topic.loc[0]

Text                                                      wondering anyone could enlighten car saw day door sport car late early really small addition front bumper separate rest body know anyone model name engine spec production car made history whatever funky looking car please mail
Cleaned_Text         [wondering, anyone, could, enlighten, car, saw, day, door, sport, car, late, early, really, small, addition, front, bumper, separate, rest, body, know, anyone, model, name, engine, spec, production, car, made, history, whatever, funky, looking, car, please, mail]
Topic                                                                                                                                                                                                                                                                                      4
high_sim_score                                                                                                                                   

**Using similarity for Checking accuracy of Manual topics**

how similar are different topics and how similar are sub topic ( ex. Computer sub topics ) 


1. Adding Title in df_Topic

In [105]:
df_Topic.columns

Index(['Text', 'Cleaned_Text', 'Topic', 'high_sim_score', 'high_sim_position',
       'high_sim_topic', 'title'],
      dtype='object')

In [104]:
df_Topic = df_Topic.join(df_Check["title"])

Getting the report

In [118]:
df_Topic.groupby(['title','high_sim_title']).agg({"high_sim_title": ['count']})

high_sim_title
                                                           count
title                    high_sim_title                         
alt.atheism              alt.atheism                         228
                         comp.graphics                         5
                         comp.os.ms-windows.misc               4
                         comp.sys.ibm.pc.hardware              2
                         comp.sys.mac.hardware                 1
                         comp.windows.x                        2
                         misc.forsale                          8
                         rec.autos                            14
                         rec.motorcycles                       6
                         rec.sport.baseball                    3
                         rec.sport.hockey                      3
                         sci.crypt                             6
                         sci.electronics                       1
                         sci.med                               8
                         sci.space                             9
                         soc.religion.christian               86
                         talk.politics.guns                   13
                         talk.politics.mideast                26
                         talk.politics.misc                   23
                         talk.religion.misc                   32
comp.graphics            alt.atheism                           3
                         comp.graphics                       327
                         comp.os.ms-windows.misc              36
                         comp.sys.ibm.pc.hardware             24
                         comp.sys.mac.hardware                27
                         comp.windows.x                       63
                         misc.forsale                         17
                         rec.autos                            23
                         rec.motorcycles                       5
                         rec.sport.baseball                    5
                         rec.sport.hockey                      4
                         sci.crypt                             6
                         sci.electronics                      14
                         sci.med                              10
                         sci.space                            11
                         soc.religion.christian                3
                         talk.politics.guns                    2
                         talk.politics.mideast                 1
                         talk.religion.misc                    3
comp.os.ms-windows.misc  alt.atheism                           3
                         comp.graphics                        42
                         comp.os.ms-windows.misc             280
                         comp.sys.ibm.pc.hardware             66
                         comp.sys.mac.hardware                37
                         comp.windows.x                       65
                         misc.forsale                         22
                         rec.autos                            33
                         rec.motorcycles                       4
                         rec.sport.baseball                    4
                         rec.sport.hockey                      5
                         sci.crypt                             5
                         sci.electronics                       9
                         sci.med                               5
                         sci.space                             4
                         soc.religion.christian                1
                         talk.politics.mideast                 3
                         talk.politics.misc                    1
                         talk.religion.misc                    2
comp.sys.ibm.pc.hardware alt.atheism                           2
                    